In [1]:
# %% init
import os
os.chdir("/home/tangir/crmbm/python/shrimp")

from IPython import get_ipython
get_ipython().magic("clear")

import matplotlib.pylab as plt
import matplotlib.dates as mdates
import mrs.reco as reco
import mrs.sim as sim
import mrs.db as db
import mrs.log as log
import mrs.aliases as xxx
import numpy as np
import pandas as pd
import seaborn as sns
from scipy import stats
import suspect
from datetime import datetime

plt.close("all")
plt.rcParams['figure.dpi'] = 75
plt.rcParams['figure.max_open_warning'] = 1000
plt.rcParams["figure.figsize"] = [8, 6]
# get_ipython().magic("matplotlib inline")
get_ipython().magic("matplotlib notebook")
log.setLevel(log.INFO)

cm = sns.color_palette("rocket", as_cmap=True)
pd.set_option('display.max_rows', 50)
pd.options.mode.chained_assignment = None  # default='warn'

(DEBUG) Loaded backend nbAgg version unknown.


# Select datasets

## Load data
Load datasets from SC and brain

In [2]:
rdb_sc = db.data_db("/home/tangir/crmbm/acq_db/sc.pkl")
rdb_brain = db.data_db("/home/tangir/crmbm/acq_db/brain.pkl")

(INFO)  data_db.__init__: initializing db files [in progress]
(INFO)  data_db.__init__: /home/tangir/crmbm/acq_db/sc.pkl
(INFO)  data_db.__init__: /home/tangir/crmbm/acq_db/sc_fit.pkl
(INFO)  data_db.__init__: initializing db files [done]
(INFO)  data_db.__init__: initializing db files [in progress]
(INFO)  data_db.__init__: /home/tangir/crmbm/acq_db/brain.pkl
(INFO)  data_db.__init__: /home/tangir/crmbm/acq_db/brain_fit.pkl
(INFO)  data_db.__init__: initializing db files [done]


In [3]:
#log.setLevel(log.DEBUG)
df = rdb_sc.extend_df_reco(True)
df_brain = rdb_brain.extend_df_reco(True)
#log.setLevel(log.INFO)

# remove db objects to free memory
del(rdb_sc)
del(rdb_brain)

df

(INFO)  data_db.extend_df_reco: extending dataframe by scraping data...
(INFO)  data_db.extend_df_reco: extending dataframe by scraping data...


patient  study  \
scan_hash                                          
5010227e1b906e17fdeac0fdff8396b2      296      1   
405976f0de3db2b1ea8b83c3accc8994      296      1   
fb81785a61e346c7fdbb37479f312ca5      300      1   
2fff316122fc89a0b4d1f918f6cd62d8      300      1   
77db8d723204884d29a997944390611b      304      1   
40ef3af628211f936a93c79adb00ac9d      307      1   
159437f4b7de93d40c7fef7853019df3      307      1   
4a3a0b1b9f85f1928b9bfb342358fef4      307      1   
1baf6b702f39fefb5ad9e44179057ef7      307      1   
a2b582b37a04bd4efc43138368bc0b96      308      1   
01a46c3d8ebdb2912567745a61ef0d24      310      1   
7cb024e470b0b2b072436635a19a1c00      311      1   
9f8067ea065153da5b3a352d58f6ca23      313      1   
0a58f85af8c32d06cbbca74391447ad2      314      1   
2195967ae34d5ef7dcfba4fc93a9e121      314      1   
fe34c6902afd341a0c81de0a0b6d6373      316      1   
5f9a42662bfe3586bee57f3ead964778      316      1   
3c700829d5feb605285c5ef7cfad4055      319      1   
f416f6db6cda52195e3b8046fc586ef2      319      1   
b9875913db5c0f321922f819401cc02e      328      1   
fc8cb0e8f7b3747a10eeabc1cf8ab9fb      329      1   
2a9fe3c48c69e575db0a8eeeb202d44d      329      1   
3695a02a4fbf0153215cf09eaa21658e      333      1   
2e9c959e58727727c1576108fb6ef2b9      336      1   
afb10548c794ebbf8bd304be1f52b0c1      338      1   
ef31f01b58b8279ef0df239b6d15a055      300      2   
62f4072c25c940cd1bfcb41a560749e2      349      1   
90a5b0c9d27daa2396d73e53f5a90afe      355      1   
42063831757801c81193689ead085d37      304      2   
8b934ce052f541a6923805395f44bfb8      304      2   
75ae13bc44bf3d55f5be46d4c59df84d      311      2   
caf8ec7f9e1026afbfa1e2c41ba43539      311      2   
355445d1bac5ee682c88f889b4c01d09      336      2   
967a1b8dace220e916df680759f31d84      336      2   
49872ea4c73b9206c804c4fdaa298ed9      336      2   
fd2940e9489a5d28773792aeb95f54e7      336      2   
90d883145e25fe54b74b05c16b56ace1      319      2   
e8481853cde6f05d66b1c43d8dd00e40      313      2   
da13ac26d45806eaced75e7dd71df1f3      333      2   
e2c8b162388ff1d24dca288885b87e4b      314      2   
45b70edaa2460689b120a7ed10a1f6e1      349      2   

                                                     dataset_legend  \
scan_hash                                                             
5010227e1b906e17fdeac0fdff8396b2                           #0 STEAM   
405976f0de3db2b1ea8b83c3accc8994                 #1 sLASER R:N=20:1   
fb81785a61e346c7fdbb37479f312ca5                 #0 sLASER R:N=25:1   
2fff316122fc89a0b4d1f918f6cd62d8            #1 sLASER R:N=25:1 trig   
77db8d723204884d29a997944390611b                          #0 crappy   
40ef3af628211f936a93c79adb00ac9d        #0 sLASER 20:1 cardiac trig   
159437f4b7de93d40c7fef7853019df3           #1 sLASER 20:1 resp trig   
4a3a0b1b9f85f1928b9bfb342358fef4             #2 sLASER 20:1 no trig   
1baf6b702f39fefb5ad9e44179057ef7  #3 sLASER 10:2 repos. + resp trig   
a2b582b37a04bd4efc43138368bc0b96           #0 sLASER 20:1 resp trig   
01a46c3d8ebdb2912567745a61ef0d24                     #0 sLASER 20:1   
7cb024e470b0b2b072436635a19a1c00                     #0 sLASER 20:1   
9f8067ea065153da5b3a352d58f6ca23                     #0 sLASER 20:1   
0a58f85af8c32d06cbbca74391447ad2                     #0 sLASER 20:1   
2195967ae34d5ef7dcfba4fc93a9e121                      #1 sLASER 5:5   
fe34c6902afd341a0c81de0a0b6d6373                     #0 sLASER 20:1   
5f9a42662bfe3586bee57f3ead964778                      #1 sLASER 5:5   
3c700829d5feb605285c5ef7cfad4055                     #0 sLASER 20:1   
f416f6db6cda52195e3b8046fc586ef2                     #1 sLASER 10:2   
b9875913db5c0f321922f819401cc02e                     #0 sLASER 20:1   
fc8cb0e8f7b3747a10eeabc1cf8ab9fb                     #0 sLASER 20:1   
2a9fe3c48c69e575db0a8eeeb202d44d                     #1 sLASER 10:2   
3695a02a4fbf0153215cf09eaa21658e                     #0 sLASER 20:1   
2e9c959e58727727c15761

## Adding additional columns
Like BMI, BFP, etc.

SNR is normalized by:
* voxel size
* number of averages (post-data-rejection)

Therefore
* SNR values are divided by voxel volume and multiplied by a mean volume to get usual SNR values
* SNR values are divided by $\sqrt(NA)$ kept after data rejection and multiplied by $\sqrt(128)$

In [4]:
import datetime
this_year = datetime.date.today().year

# create a patient*study id number
df["patient_study_id"] = df["patient"].astype(str) + "_" + df["study"].astype(str)
df_brain["patient_study_id"] = df_brain["patient"].astype(str) + "_" + df_brain["study"].astype(str)

# calculate bmi
df["dataset_patient_bmi"] = df["dataset_raw_data__patient_weight"] / \
    df["dataset_raw_data__patient_height"]**2

# calculate BFP (IMG)
df["dataset_patient_bfp"] = 1.39 * df["dataset_patient_bmi"]
+ 0.16 * (this_year - pd.DatetimeIndex(df["dataset_raw_data__patient_birthday"]).year)
- 10.34 * (df["dataset_raw_data__patient_sex"] == "M").astype(int)
- 9

# SNR
# final estimations
df["dataset_snr_final"] = df["dataset_raw_analysis-results_cropping_snr"]
df["dataset_lw"] = df["dataset_raw_analysis-results_cropping_lw"]
df["dataset_snr_norm"] = df["dataset_raw_analysis-results_cropping_snr"]

# VOI normalization
# calculate voxel volume
df["dataset_voxel_vol_cm3"] = (np.array(list(df["dataset_raw_data_voxel_dimensions"])) / 10.0).prod()
mean_voxel_vol = df["dataset_voxel_vol_cm3"].mean()
df["dataset_snr_norm"] = df["dataset_snr_norm"] / df["dataset_voxel_vol_cm3"] * mean_voxel_vol

# NA normalization
na_norm = 128.0
df["dataset_snr_norm"] = df["dataset_snr_norm"] / np.sqrt(df["dataset_raw_data__data_rejection[0]_Post-rejection_na"]) * np.sqrt(na_norm)

# signal stability
df["dataset_prerej_amplitude_mean"] = [s[:,0].mean(axis=0) if(type(s) != np.float) else np.nan for s in df["dataset_raw_data__data_rejection[0]_Pre-rejection_measurements"]]
df["dataset_prerej_amplitude_std"] = [s[:,0].std(axis=0) if(type(s) != np.float) else np.nan for s in df["dataset_raw_data__data_rejection[0]_Pre-rejection_measurements"]]
df["dataset_prerej_linewidth_mean"] = [s[:,1].mean(axis=0) if(type(s) != np.float) else np.nan for s in df["dataset_raw_data__data_rejection[0]_Pre-rejection_measurements"]]
df["dataset_prerej_linewidth_std"] = [s[:,1].std(axis=0) if(type(s) != np.float) else np.nan for s in df["dataset_raw_data__data_rejection[0]_Pre-rejection_measurements"]]
df["dataset_prerej_chemical_shift_mean"] = [s[:,2].mean(axis=0) if(type(s) != np.float) else np.nan for s in df["dataset_raw_data__data_rejection[0]_Pre-rejection_measurements"]]
df["dataset_prerej_chemical_shift_std"] = [s[:,2].std(axis=0) if(type(s) != np.float) else np.nan for s in df["dataset_raw_data__data_rejection[0]_Pre-rejection_measurements"]]
df["dataset_prerej_phase_mean"] = [s[:,3].mean(axis=0) if(type(s) != np.float) else np.nan for s in df["dataset_raw_data__data_rejection[0]_Pre-rejection_measurements"]]
df["dataset_prerej_phase_std"] = [s[:,3].std(axis=0) if(type(s) != np.float) else np.nan for s in df["dataset_raw_data__data_rejection[0]_Pre-rejection_measurements"]]

# calculate theoretical scan time knowing NA and TR, neglicting resp. trig
df["dataset_acqtime"] = df["dataset_raw_data__sequence_tr"] / 1000.0 * (df["dataset_raw_data__sequence_na"] + df["dataset_raw_data__sequence_ds"])
df["dataset_acqtime_eff"] = df["dataset_dcm_data__sequence_eff_acquisition_time"]

# calculating data rejection rate
df["dataset_rejection_rate_prct"] = (df["dataset_raw_data__data_rejection[0]_Pre-rejection_na"] - 
 df["dataset_raw_data__data_rejection[0]_Post-rejection_na"]) / df["dataset_raw_data__data_rejection[0]_Pre-rejection_na"] * 100.0

# estimate artefact intensity for each dataset
df["dataset_artefact_signal"] = np.array([o.analyze_snr_1d([4.9, 5.5], [-2, -1], True, True) for o in df["dataset_raw_data_obj"]])[:, 1]

# estimate water intensity for each dataset
df["dataset_water_signal"] = np.array([o.analyze_snr_1d([4.6, 4.8], [-2, -1], True, True) for o in df["dataset_raw_data_obj"]])[:, 1]

df

<IPython.core.display.Javascript object>

(INFO)  MRSData2.analyze_snr_1d: results for [#0 STEAM [RAW]] coming...
(INFO)  MRSData2.analyze_snr_1d: S = 3.54E+03, N = 1.86E+02, SNR = 18.99!
(INFO)  MRSData2.analyze_snr_1d: results for [#1 sLASER R:N=20:1 [RAW]] coming...
(INFO)  MRSData2.analyze_snr_1d: S = 6.20E+03, N = 1.75E+02, SNR = 35.38!
(INFO)  MRSData2.analyze_snr_1d: results for [#0 sLASER R:N=25:1 [RAW]] coming...
(INFO)  MRSData2.analyze_snr_1d: S = 7.36E+03, N = 1.90E+02, SNR = 38.85!
(INFO)  MRSData2.analyze_snr_1d: results for [#1 sLASER R:N=25:1 trig [RAW]] coming...
(INFO)  MRSData2.analyze_snr_1d: S = 7.21E+03, N = 1.89E+02, SNR = 38.17!
(INFO)  MRSData2.analyze_snr_1d: results for [#0 crappy [DCM]] coming...
(INFO)  MRSData2.analyze_snr_1d: S = 1.08E+04, N = 1.02E+02, SNR = 105.83!
(INFO)  MRSData2.analyze_snr_1d: results for [#0 sLASER 20:1 cardiac trig [RAW]] coming...
(INFO)  MRSData2.analyze_snr_1d: S = 6.05E+03, N = 3.31E+02, SNR = 18.28!
(INFO)  MRSData2.analyze_snr_1d: results for [#1 sLASER 20:1 resp tr

(INFO)  MRSData2.analyze_snr_1d: results for [#0 sLASER 20:1 [RAW]] coming...
(INFO)  MRSData2.analyze_snr_1d: S = 8.17E+04, N = 2.11E+02, SNR = 387.18!
(INFO)  MRSData2.analyze_snr_1d: results for [#0 sLASER 20:1 [RAW]] coming...
(INFO)  MRSData2.analyze_snr_1d: S = 2.87E+04, N = 4.59E+02, SNR = 62.45!
(INFO)  MRSData2.analyze_snr_1d: results for [#0 sLASER 20:1 [RAW]] coming...
(INFO)  MRSData2.analyze_snr_1d: S = 8.17E+04, N = 2.14E+02, SNR = 382.24!
(INFO)  MRSData2.analyze_snr_1d: results for [#1 sLASER 5:5 [RAW]] coming...
(INFO)  MRSData2.analyze_snr_1d: S = 6.48E+04, N = 2.86E+02, SNR = 226.72!
(INFO)  MRSData2.analyze_snr_1d: results for [#0 sLASER 20:1 [RAW]] coming...
(INFO)  MRSData2.analyze_snr_1d: S = 2.93E+04, N = 2.27E+02, SNR = 128.88!
(INFO)  MRSData2.analyze_snr_1d: results for [#1 sLASER 5:5 [RAW]] coming...
(INFO)  MRSData2.analyze_snr_1d: S = 4.08E+04, N = 2.32E+02, SNR = 175.67!
(INFO)  MRSData2.analyze_snr_1d: results for [#0 sLASER 20:1 [RAW]] coming...
(INFO) 

patient  study  \
scan_hash                                          
5010227e1b906e17fdeac0fdff8396b2      296      1   
405976f0de3db2b1ea8b83c3accc8994      296      1   
fb81785a61e346c7fdbb37479f312ca5      300      1   
2fff316122fc89a0b4d1f918f6cd62d8      300      1   
77db8d723204884d29a997944390611b      304      1   
40ef3af628211f936a93c79adb00ac9d      307      1   
159437f4b7de93d40c7fef7853019df3      307      1   
4a3a0b1b9f85f1928b9bfb342358fef4      307      1   
1baf6b702f39fefb5ad9e44179057ef7      307      1   
a2b582b37a04bd4efc43138368bc0b96      308      1   
01a46c3d8ebdb2912567745a61ef0d24      310      1   
7cb024e470b0b2b072436635a19a1c00      311      1   
9f8067ea065153da5b3a352d58f6ca23      313      1   
0a58f85af8c32d06cbbca74391447ad2      314      1   
2195967ae34d5ef7dcfba4fc93a9e121      314      1   
fe34c6902afd341a0c81de0a0b6d6373      316      1   
5f9a42662bfe3586bee57f3ead964778      316      1   
3c700829d5feb605285c5ef7cfad4055      319      1   
f416f6db6cda52195e3b8046fc586ef2      319      1   
b9875913db5c0f321922f819401cc02e      328      1   
fc8cb0e8f7b3747a10eeabc1cf8ab9fb      329      1   
2a9fe3c48c69e575db0a8eeeb202d44d      329      1   
3695a02a4fbf0153215cf09eaa21658e      333      1   
2e9c959e58727727c1576108fb6ef2b9      336      1   
afb10548c794ebbf8bd304be1f52b0c1      338      1   
ef31f01b58b8279ef0df239b6d15a055      300      2   
62f4072c25c940cd1bfcb41a560749e2      349      1   
90a5b0c9d27daa2396d73e53f5a90afe      355      1   
42063831757801c81193689ead085d37      304      2   
8b934ce052f541a6923805395f44bfb8      304      2   
75ae13bc44bf3d55f5be46d4c59df84d      311      2   
caf8ec7f9e1026afbfa1e2c41ba43539      311      2   
355445d1bac5ee682c88f889b4c01d09      336      2   
967a1b8dace220e916df680759f31d84      336      2   
49872ea4c73b9206c804c4fdaa298ed9      336      2   
fd2940e9489a5d28773792aeb95f54e7      336      2   
90d883145e25fe54b74b05c16b56ace1      319      2   
e8481853cde6f05d66b1c43d8dd00e40      313      2   
da13ac26d45806eaced75e7dd71df1f3      333      2   
e2c8b162388ff1d24dca288885b87e4b      314      2   
45b70edaa2460689b120a7ed10a1f6e1      349      2   

                                                     dataset_legend  \
scan_hash                                                             
5010227e1b906e17fdeac0fdff8396b2                           #0 STEAM   
405976f0de3db2b1ea8b83c3accc8994                 #1 sLASER R:N=20:1   
fb81785a61e346c7fdbb37479f312ca5                 #0 sLASER R:N=25:1   
2fff316122fc89a0b4d1f918f6cd62d8            #1 sLASER R:N=25:1 trig   
77db8d723204884d29a997944390611b                          #0 crappy   
40ef3af628211f936a93c79adb00ac9d        #0 sLASER 20:1 cardiac trig   
159437f4b7de93d40c7fef7853019df3           #1 sLASER 20:1 resp trig   
4a3a0b1b9f85f1928b9bfb342358fef4             #2 sLASER 20:1 no trig   
1baf6b702f39fefb5ad9e44179057ef7  #3 sLASER 10:2 repos. + resp trig   
a2b582b37a04bd4efc43138368bc0b96           #0 sLASER 20:1 resp trig   
01a46c3d8ebdb2912567745a61ef0d24                     #0 sLASER 20:1   
7cb024e470b0b2b072436635a19a1c00                     #0 sLASER 20:1   
9f8067ea065153da5b3a352d58f6ca23                     #0 sLASER 20:1   
0a58f85af8c32d06cbbca74391447ad2                     #0 sLASER 20:1   
2195967ae34d5ef7dcfba4fc93a9e121                      #1 sLASER 5:5   
fe34c6902afd341a0c81de0a0b6d6373                     #0 sLASER 20:1   
5f9a42662bfe3586bee57f3ead964778                      #1 sLASER 5:5   
3c700829d5feb605285c5ef7cfad4055                     #0 sLASER 20:1   
f416f6db6cda52195e3b8046fc586ef2                     #1 sLASER 10:2   
b9875913db5c0f321922f819401cc02e                     #0 sLASER 20:1   
fc8cb0e8f7b3747a10eeabc1cf8ab9fb                     #0 sLASER 20:1   
2a9fe3c48c69e575db0a8eeeb202d44d                     #1 sLASER 10:2   
3695a02a4fbf0153215cf09eaa21658e                     #0 sLASER 20:1   
2e9c959e58727727c15761

## Fix LW for one dataset

In [5]:
scan_hash_bad_lw = df.loc[df["dataset_lw"] > 100].index[0]
# get MRSData2 obj
s = df.at[scan_hash_bad_lw, "dataset_raw_data_obj"]
# remove artefact
s = s.correct_water_removal_1d(5, [4.75, 5.5], True)
this_lw = s.analyze_linewidth_1d([4.5, 5], False, True)
df.at[scan_hash_bad_lw, "dataset_lw"] = this_lw

removing residual water peak with HSVD: ██████████████████████████████

<IPython.core.display.Javascript object>

(WARNING) No handles with labels found to put in legend.


 done.


(INFO)  MRSData2.analyze_linewidth_1d: results for [#0 sLASER 20:1 [DCM]] coming...
(INFO)  MRSData2.analyze_linewidth_1d: LW = 19.53 Hz!


<IPython.core.display.Javascript object>

## Keep only resp-gating sLASER scans
Keep only:
* semi-LASER scans
* with resp gating
and check that it does not remove any patient of study

In [6]:
n_patient_study_before_filtering = df["patient_study_id"].nunique()

# keep this for big stats about data quality
df_slaser = df.loc[(df["dataset_raw_data__sequence_name"] == "eja_svs_slaser")]
df_brain_slaser = df_brain.loc[df_brain["dataset_raw_data__sequence_name"] == "eja_svs_slaser"]

df_slaser_resptrig = df.loc[(df["dataset_raw_data__sequence_name"] == "eja_svs_slaser")
                          & (df["dataset_raw_data__sequence_gating_mode"] == sim.gating_signal_source.RESP_GATING)]

df_removed = df.loc[(df["dataset_raw_data__sequence_name"] != "eja_svs_slaser")
                  | (df["dataset_raw_data__sequence_gating_mode"] != sim.gating_signal_source.RESP_GATING)]

# check that we did not remove any patient/study
n_patient_study_after_filtering = df_slaser_resptrig["patient_study_id"].nunique()

df_removed

patient  study  \
scan_hash                                          
5010227e1b906e17fdeac0fdff8396b2      296      1   
405976f0de3db2b1ea8b83c3accc8994      296      1   
fb81785a61e346c7fdbb37479f312ca5      300      1   
77db8d723204884d29a997944390611b      304      1   
40ef3af628211f936a93c79adb00ac9d      307      1   
4a3a0b1b9f85f1928b9bfb342358fef4      307      1   
90a5b0c9d27daa2396d73e53f5a90afe      355      1   
caf8ec7f9e1026afbfa1e2c41ba43539      311      2   
355445d1bac5ee682c88f889b4c01d09      336      2   
49872ea4c73b9206c804c4fdaa298ed9      336      2   
fd2940e9489a5d28773792aeb95f54e7      336      2   

                                                dataset_legend  \
scan_hash                                                        
5010227e1b906e17fdeac0fdff8396b2                      #0 STEAM   
405976f0de3db2b1ea8b83c3accc8994            #1 sLASER R:N=20:1   
fb81785a61e346c7fdbb37479f312ca5            #0 sLASER R:N=25:1   
77db8d723204884d29a997944390611b                     #0 crappy   
40ef3af628211f936a93c79adb00ac9d   #0 sLASER 20:1 cardiac trig   
4a3a0b1b9f85f1928b9bfb342358fef4        #2 sLASER 20:1 no trig   
90a5b0c9d27daa2396d73e53f5a90afe             #0 sLASER TE=52ms   
caf8ec7f9e1026afbfa1e2c41ba43539  #1 sLASER 20/1 NA=128 notrig   
355445d1bac5ee682c88f889b4c01d09   #0 sLASER 10/2 NA=64 notrig   
49872ea4c73b9206c804c4fdaa298ed9   #1 sLASER 20/1 NA=64 notrig   
fd2940e9489a5d28773792aeb95f54e7    #2 sLASER 5/5 NA=64 notrig   

                                                               dataset_raw_files[0]  \
scan_hash                                                                             
5010227e1b906e17fdeac0fdff8396b2  /home/tangir/crmbm/acq_twix/296_ym_p1_brainmoe...   
405976f0de3db2b1ea8b83c3accc8994  /home/tangir/crmbm/acq_twix/296_ym_p1_brainmoe...   
fb81785a61e346c7fdbb37479f312ca5  /home/tangir/crmbm/acq_twix/300-pm-p1-moelle/m...   
77db8d723204884d29a997944390611b  /home/tangir/crmbm/acq/304-ka-p1-moelle/201908...   
40ef3af628211f936a93c79adb00ac9d  /home/tangir/crmbm/acq_twix/307-AP-P1-MOELLE/m...   
4a3a0b1b9f85f1928b9bfb342358fef4  /home/tangir/crmbm/acq_twix/307-AP-P1-MOELLE/m...   
90a5b0c9d27daa2396d73e53f5a90afe  /home/tangir/crmbm/acq_twix/355-st-p1-moelle/m...   
caf8ec7f9e1026afbfa1e2c41ba43539  /home/tangir/crmbm/acq_twix/311-sl-p2-moelle/m...   
355445d1bac5ee682c88f889b4c01d09  /home/tangir/crmbm/acq_twix/336-nb-p2-moelle/m...   
49872ea4c73b9206c804c4fdaa298ed9  /home/tangir/crmbm/acq_twix/336-nb-p2-moelle/m...   
fd2940e9489a5d28773792aeb95f54e7  /home/tangir/crmbm/acq_twix/336-nb-p2-moelle/m...   

                                                               dataset_raw_files[1]  \
scan_hash                                                                             
5010227e1b906e17fdeac0fdff8396b2  /home/tangir/crmbm/acq_twix/296_ym_p1_brainmoe...   
405976f0de3db2b1ea8b83c3accc8994  /home/tangir/crmbm/acq_twix/296_ym_p1_brainmoe...   
fb81785a61e346c7fdbb37479f312ca5  /home/tangir/crmbm/acq_twix/300-pm-p1-moelle/m...   
77db8d723204884d29a997944390611b  /home/tangir/crmbm/acq/304-ka-p1-moelle/201908...   
40ef3af628211f936a93c79adb00ac9d  /home/tangir/crmbm/acq_twix/307-AP-P1-MOELLE/m...   
4a3a0b1b9f85f1928b9bfb342358fef4  /home/tangir/crmbm/acq_twix/307-AP-P1-MOELLE/m...   
90a5b0c9d27daa2396d73e53f5a90afe  /home/tangir/crmbm/acq_twix/355-st-p1-moelle/m...   
caf8ec7f9e1026afbfa1e2c41ba43539  /home/tangir/crmbm/acq_twix/311-sl-p2-moelle/m...   
355445d1bac5ee682c88f889b4c01d09  /home/tangir/crmbm/acq_twix/336-nb-p2-moelle/m...   
49872ea4c73b9206c804c4fdaa298ed9  /home/tangir/crmbm/acq_twix/336-nb-p2-moelle/m...   
fd2940e9489a5d28773792aeb95f54e7  /home/tangir/crmbm/acq_twix/336-nb-p2-moelle/m...   

                                                               dataset_raw_data_obj  \
scan_hash                                                                             
5010227e1b906e17fdeac0fdff8396b2  [(5.906507327308433+113.60

In [7]:
if(n_patient_study_before_filtering != n_patient_study_after_filtering):
    log.warning("we removed some patient or study from the db: %d vs %d" % (n_patient_study_before_filtering, n_patient_study_after_filtering))


(WARNING) <ipython-input-7-b04a913462c2>.<module>: we removed some patient or study from the db: 27 vs 24


I have been going over the datasets rejected here:

* 296_ym_p1_brainmoelle: one of the first SC scans, was not resp gating at the time, too bad but only P1 (no P2)
* 300_pm_p1_moelle: removing one no gating scan, there is another one with trig so OK
* 304_ka_p1_moelle: removing this P1 study (there is a P2 that will be considered P1), data was crappy, dicom only, and no trig for some reason
* 307_ap_p1_moelle: removing 2 scans (no trig and cardiac trig) that were done for tests, still a 2 resp trig left)
* 355_st_p1_moelle: removing scan and therefore patient, no resp trig because I was in hurry. Too bad, the data is not soo bad and it was a fat guy (cohort stats) :(
* 311_sl_p2_moelle, 336_nb_p2_moelle: just some trig tests removed, no patient or study removed

So removed 3 patient or study in total because not following the standard protocol (semiLASER + resp gating)

## Remove strong artefact datasets
Criteria: when the artefact is stronger than the residual water peak

In [8]:
df = df_slaser_resptrig
df_strong_artefact_to_remove=df.loc[ (df["dataset_artefact_signal"] > df["dataset_water_signal"])  ]
df_no_artefact = df.drop(df_strong_artefact_to_remove.index)
df_strong_artefact_to_remove

patient  study  \
scan_hash                                          
3695a02a4fbf0153215cf09eaa21658e      333      1   
42063831757801c81193689ead085d37      304      2   
8b934ce052f541a6923805395f44bfb8      304      2   

                                                 dataset_legend  \
scan_hash                                                         
3695a02a4fbf0153215cf09eaa21658e                 #0 sLASER 20:1   
42063831757801c81193689ead085d37  #0 1st try (30-40Hz water LW)   
8b934ce052f541a6923805395f44bfb8     #1 2nd try (25Hz water LW)   

                                                               dataset_raw_files[0]  \
scan_hash                                                                             
3695a02a4fbf0153215cf09eaa21658e  /home/tangir/crmbm/acq/333-sc-p1-moelle/201911...   
42063831757801c81193689ead085d37  /home/tangir/crmbm/acq_twix/304-ka-p2-moelle/m...   
8b934ce052f541a6923805395f44bfb8  /home/tangir/crmbm/acq_twix/304-ka-p2-moelle/m...   

                                                               dataset_raw_files[1]  \
scan_hash                                                                             
3695a02a4fbf0153215cf09eaa21658e  /home/tangir/crmbm/acq/333-sc-p1-moelle/201911...   
42063831757801c81193689ead085d37  /home/tangir/crmbm/acq_twix/304-ka-p2-moelle/m...   
8b934ce052f541a6923805395f44bfb8  /home/tangir/crmbm/acq_twix/304-ka-p2-moelle/m...   

                                                               dataset_raw_data_obj  \
scan_hash                                                                             
3695a02a4fbf0153215cf09eaa21658e  [(5208.6240234375+896.160888671875j), (4583.44...   
42063831757801c81193689ead085d37  [(3219.131539558533+199.63577279252735j), (327...   
8b934ce052f541a6923805395f44bfb8  [(2954.9663979595907-158.85486067839136j), (29...   

                                  dataset_raw_data__dt  dataset_raw_data__f0  \
scan_hash                                                                      
3695a02a4fbf0153215cf09eaa21658e                0.0002            297.205455   
42063831757801c81193689ead085d37                0.0001            297.204932   
8b934ce052f541a6923805395f44bfb8                0.0001            297.204932   

                                  dataset_raw_data__te  dataset_raw_data__tr  \
scan_hash                                                                      
3695a02a4fbf0153215cf09eaa21658e                 45.96                4130.0   
42063831757801c81193689ead085d37                 43.96                4170.0   
8b934ce052f541a6923805395f44bfb8                 52.48                4690.0   

                                  ...  dataset_prerej_linewidth_std  \
scan_hash                         ...                                 
3695a02a4fbf0153215cf09eaa21658e  ...                           NaN   
42063831757801c81193689ead085d37  ...                      3.422733   
8b934ce052f541a6923805395f44bfb8  ...                      3.239967   

                                 dataset_prerej_chemical_shift_mean  \
scan_hash                                                             
3695a02a4fbf0153215cf09eaa21658e                                NaN   
42063831757801c81193689ead085d37                      -2.220446e-16   
8b934ce052f541a6923805395f44bfb8                       4.440892e-16   

                                 dataset_prerej_chemical_shift_std  \
scan_hash                                                            
3695a02a4fbf0153215cf09eaa21658e                               NaN   
42063831757801c81193689ead085d37                          0.019246   
8b934ce052f541a6923805395f44bfb8                          0.023075   

                                 dataset_prerej_phase_mean  \
scan_hash                                                    
3695a02a4fbf0153215cf09eaa21658e                       NaN   
42063831757801c81193689ead085d37             -4.625929e-18   
8b934ce052f541a6

## Find any orphan P2 studies
and set them as P1 :)

In [9]:
# using previously filtered db
df = df_no_artefact

# init new df
df_orphan_p2_fix = pd.DataFrame(columns=df.columns)

# browse the df
for this_index, this_row in df.iterrows():
    # if meet a P2 study
    if(this_row["study"] == 2):
        # get the patient
        this_patient = this_row["patient"]
        # find corresponding P1
        df_patient_p1 = df.loc[(df["patient"] == this_patient)
                             & (df["study"] == 1)]
        # if empty
        if(df_patient_p1.empty):
            # change the P2 we are on into a P1
            this_row["study"] = 1
    
    # store it
    df_orphan_p2_fix = df_orphan_p2_fix.append([this_row])
        
        
df_orphan_p2_fix

patient study  \
2fff316122fc89a0b4d1f918f6cd62d8     300     1   
159437f4b7de93d40c7fef7853019df3     307     1   
1baf6b702f39fefb5ad9e44179057ef7     307     1   
a2b582b37a04bd4efc43138368bc0b96     308     1   
01a46c3d8ebdb2912567745a61ef0d24     310     1   
7cb024e470b0b2b072436635a19a1c00     311     1   
9f8067ea065153da5b3a352d58f6ca23     313     1   
0a58f85af8c32d06cbbca74391447ad2     314     1   
2195967ae34d5ef7dcfba4fc93a9e121     314     1   
fe34c6902afd341a0c81de0a0b6d6373     316     1   
5f9a42662bfe3586bee57f3ead964778     316     1   
3c700829d5feb605285c5ef7cfad4055     319     1   
f416f6db6cda52195e3b8046fc586ef2     319     1   
b9875913db5c0f321922f819401cc02e     328     1   
fc8cb0e8f7b3747a10eeabc1cf8ab9fb     329     1   
2a9fe3c48c69e575db0a8eeeb202d44d     329     1   
2e9c959e58727727c1576108fb6ef2b9     336     1   
afb10548c794ebbf8bd304be1f52b0c1     338     1   
ef31f01b58b8279ef0df239b6d15a055     300     2   
62f4072c25c940cd1bfcb41a560749e2     349     1   
75ae13bc44bf3d55f5be46d4c59df84d     311     2   
967a1b8dace220e916df680759f31d84     336     2   
90d883145e25fe54b74b05c16b56ace1     319     2   
e8481853cde6f05d66b1c43d8dd00e40     313     2   
da13ac26d45806eaced75e7dd71df1f3     333     1   
e2c8b162388ff1d24dca288885b87e4b     314     2   
45b70edaa2460689b120a7ed10a1f6e1     349     2   

                                                     dataset_legend  \
2fff316122fc89a0b4d1f918f6cd62d8            #1 sLASER R:N=25:1 trig   
159437f4b7de93d40c7fef7853019df3           #1 sLASER 20:1 resp trig   
1baf6b702f39fefb5ad9e44179057ef7  #3 sLASER 10:2 repos. + resp trig   
a2b582b37a04bd4efc43138368bc0b96           #0 sLASER 20:1 resp trig   
01a46c3d8ebdb2912567745a61ef0d24                     #0 sLASER 20:1   
7cb024e470b0b2b072436635a19a1c00                     #0 sLASER 20:1   
9f8067ea065153da5b3a352d58f6ca23                     #0 sLASER 20:1   
0a58f85af8c32d06cbbca74391447ad2                     #0 sLASER 20:1   
2195967ae34d5ef7dcfba4fc93a9e121                      #1 sLASER 5:5   
fe34c6902afd341a0c81de0a0b6d6373                     #0 sLASER 20:1   
5f9a42662bfe3586bee57f3ead964778                      #1 sLASER 5:5   
3c700829d5feb605285c5ef7cfad4055                     #0 sLASER 20:1   
f416f6db6cda52195e3b8046fc586ef2                     #1 sLASER 10:2   
b9875913db5c0f321922f819401cc02e                     #0 sLASER 20:1   
fc8cb0e8f7b3747a10eeabc1cf8ab9fb                     #0 sLASER 20:1   
2a9fe3c48c69e575db0a8eeeb202d44d                     #1 sLASER 10:2   
2e9c959e58727727c1576108fb6ef2b9                     #0 sLASER 20:1   
afb10548c794ebbf8bd304be1f52b0c1                  #0 sLASER 20:1 WS   
ef31f01b58b8279ef0df239b6d15a055      #0 sLASER 20:1 (REF with OVS)   
62f4072c25c940cd1bfcb41a560749e2      #0 sLASER 10:2 (REF with OVS)   
75ae13bc44bf3d55f5be46d4c59df84d         #0 sLASER 20/1 NA=128 trig   
967a1b8dace220e916df680759f31d84         #0 sLASER 20/1 NA=128 trig   
90d883145e25fe54b74b05c16b56ace1          #0 sLASER 10/2 NA=64 trig   
e8481853cde6f05d66b1c43d8dd00e40                     #0 sLASER 20/1   
da13ac26d45806eaced75e7dd71df1f3                     #0 sLASER 20/1   
e2c8b162388ff1d24dca288885b87e4b              #0 sLASER 20/1 NA=128   
45b70edaa2460689b120a7ed10a1f6e1              #0 sLASER 10/2 NA=128   

                                                               dataset_raw_files[0]  \
2fff316122fc89a0b4d1f918f6cd62d8  /home/tangir/crmbm/acq_twix/300-pm-p1-moelle/m...   
159437f4b7de93d40c7fef7853019df3  /home/tangir/crmbm/acq_twix/307-AP-P1-MOELLE/m...   
1baf6b702f39fefb5ad9e44179057ef7  /home/tangir/crmbm/acq_twix/307-AP-P1-MOELLE/m...   
a2b582b37a04bd4efc43138368bc0b96  /home/tangir/crmbm/acq_twix/308-rs-p1-moelle/m...   
01a46c3d8ebdb2912567745a61ef0d24  /home/tangir/crmbm/acq_twix/310-mg-p1-moelle/m...   
7cb024e470b0b2b072436635a19a1c00  /home/tangir/crmbm/acq_twix/311-sl-p1-moelle/m...   
9f8067ea065153da5b3a352d58f6ca23  

## Keep only one scan per study
Now, on resp-gating sLASER, keep only one scan per study based on SNR and LW. This is the core group that will be used for the paper's stats.

In [10]:
# using previously filtered db
df = df_orphan_p2_fix

n_patient_study_before_filtering = df["patient_study_id"].nunique()

df_onescan_per_study = pd.DataFrame(columns=df.columns)
patient_study_id_done = []
for this_index, this_row in df.iterrows():
    # find duplicates
    if(this_row["patient_study_id"] not in patient_study_id_done):
        this_df_dup = df.loc[df["patient_study_id"] == this_row["patient_study_id"]]
        this_df_dup_best_snr = this_df_dup.loc[this_df_dup["dataset_raw_analysis-results_cropping_snr"] == this_df_dup["dataset_raw_analysis-results_cropping_snr"].max()]
        df_onescan_per_study = df_onescan_per_study.append([this_df_dup_best_snr])
        patient_study_id_done.append(this_row["patient_study_id"])

n_patient_study_after_filtering = df_onescan_per_study["patient_study_id"].nunique()

if(n_patient_study_before_filtering != n_patient_study_after_filtering):
    log.warning("we removed some patient or study from the db: %d vs %d" % (n_patient_study_before_filtering, n_patient_study_after_filtering))

df_onescan_per_study

patient study  \
2fff316122fc89a0b4d1f918f6cd62d8     300     1   
1baf6b702f39fefb5ad9e44179057ef7     307     1   
a2b582b37a04bd4efc43138368bc0b96     308     1   
01a46c3d8ebdb2912567745a61ef0d24     310     1   
7cb024e470b0b2b072436635a19a1c00     311     1   
9f8067ea065153da5b3a352d58f6ca23     313     1   
0a58f85af8c32d06cbbca74391447ad2     314     1   
5f9a42662bfe3586bee57f3ead964778     316     1   
f416f6db6cda52195e3b8046fc586ef2     319     1   
b9875913db5c0f321922f819401cc02e     328     1   
fc8cb0e8f7b3747a10eeabc1cf8ab9fb     329     1   
2e9c959e58727727c1576108fb6ef2b9     336     1   
afb10548c794ebbf8bd304be1f52b0c1     338     1   
ef31f01b58b8279ef0df239b6d15a055     300     2   
62f4072c25c940cd1bfcb41a560749e2     349     1   
75ae13bc44bf3d55f5be46d4c59df84d     311     2   
967a1b8dace220e916df680759f31d84     336     2   
90d883145e25fe54b74b05c16b56ace1     319     2   
e8481853cde6f05d66b1c43d8dd00e40     313     2   
da13ac26d45806eaced75e7dd71df1f3     333     1   
e2c8b162388ff1d24dca288885b87e4b     314     2   
45b70edaa2460689b120a7ed10a1f6e1     349     2   

                                                     dataset_legend  \
2fff316122fc89a0b4d1f918f6cd62d8            #1 sLASER R:N=25:1 trig   
1baf6b702f39fefb5ad9e44179057ef7  #3 sLASER 10:2 repos. + resp trig   
a2b582b37a04bd4efc43138368bc0b96           #0 sLASER 20:1 resp trig   
01a46c3d8ebdb2912567745a61ef0d24                     #0 sLASER 20:1   
7cb024e470b0b2b072436635a19a1c00                     #0 sLASER 20:1   
9f8067ea065153da5b3a352d58f6ca23                     #0 sLASER 20:1   
0a58f85af8c32d06cbbca74391447ad2                     #0 sLASER 20:1   
5f9a42662bfe3586bee57f3ead964778                      #1 sLASER 5:5   
f416f6db6cda52195e3b8046fc586ef2                     #1 sLASER 10:2   
b9875913db5c0f321922f819401cc02e                     #0 sLASER 20:1   
fc8cb0e8f7b3747a10eeabc1cf8ab9fb                     #0 sLASER 20:1   
2e9c959e58727727c1576108fb6ef2b9                     #0 sLASER 20:1   
afb10548c794ebbf8bd304be1f52b0c1                  #0 sLASER 20:1 WS   
ef31f01b58b8279ef0df239b6d15a055      #0 sLASER 20:1 (REF with OVS)   
62f4072c25c940cd1bfcb41a560749e2      #0 sLASER 10:2 (REF with OVS)   
75ae13bc44bf3d55f5be46d4c59df84d         #0 sLASER 20/1 NA=128 trig   
967a1b8dace220e916df680759f31d84         #0 sLASER 20/1 NA=128 trig   
90d883145e25fe54b74b05c16b56ace1          #0 sLASER 10/2 NA=64 trig   
e8481853cde6f05d66b1c43d8dd00e40                     #0 sLASER 20/1   
da13ac26d45806eaced75e7dd71df1f3                     #0 sLASER 20/1   
e2c8b162388ff1d24dca288885b87e4b              #0 sLASER 20/1 NA=128   
45b70edaa2460689b120a7ed10a1f6e1              #0 sLASER 10/2 NA=128   

                                                               dataset_raw_files[0]  \
2fff316122fc89a0b4d1f918f6cd62d8  /home/tangir/crmbm/acq_twix/300-pm-p1-moelle/m...   
1baf6b702f39fefb5ad9e44179057ef7  /home/tangir/crmbm/acq_twix/307-AP-P1-MOELLE/m...   
a2b582b37a04bd4efc43138368bc0b96  /home/tangir/crmbm/acq_twix/308-rs-p1-moelle/m...   
01a46c3d8ebdb2912567745a61ef0d24  /home/tangir/crmbm/acq_twix/310-mg-p1-moelle/m...   
7cb024e470b0b2b072436635a19a1c00  /home/tangir/crmbm/acq_twix/311-sl-p1-moelle/m...   
9f8067ea065153da5b3a352d58f6ca23  /home/tangir/crmbm/acq_twix/313-ft-p1-moelle/m...   
0a58f85af8c32d06cbbca74391447ad2  /home/tangir/crmbm/acq_twix/314-yt-p1-moelle/m...   
5f9a42662bfe3586bee57f3ead964778  /home/tangir/crmbm/acq_twix/316-ap-p1-moelle/m...   
f416f6db6cda52195e3b8046fc586ef2  /home/tangir/crmbm/acq_twix/319-fc-p1-moelle/m...   
b9875913db5c0f321922f819401cc02e  /home/tangir/crmbm/acq_twix/328-af-p1-moelle/m...   
fc8cb0e8f7b3747a10eeabc1cf8ab9fb  /home/tangir/crmbm/acq_twix/329-pi-p1-moelle/m...   
2e9c959e58727727c1576108fb6ef2b9  /home/tangir/crmbm/acq_twix/336-nb-p1-moelle/m...   
afb10548c794ebbf8bd304be1f52b0c1  /home/tangir/crmbm/acq_twix/338-ro-p1-moelle/m...   
ef31f01b58b8279ef0df239b6d15a0

Now on brain data:

In [11]:
# using previously filtered db
df = df_brain_slaser

df_brain_onescan_per_study = pd.DataFrame(columns=df.columns)
patient_study_id_done = []
for this_index, this_row in df.iterrows():
    # find duplicates
    if(this_row["patient_study_id"] not in patient_study_id_done):
        this_df_dup = df.loc[df["patient_study_id"] == this_row["patient_study_id"]]
        this_df_dup_best_snr = this_df_dup.loc[this_df_dup["dataset_raw_analysis-results_cropping_snr"] == this_df_dup["dataset_raw_analysis-results_cropping_snr"].max()]
        df_brain_onescan_per_study = df_brain_onescan_per_study.append([this_df_dup_best_snr])
        patient_study_id_done.append(this_row["patient_study_id"])

df_brain_onescan_per_study

patient study  \
b057a3e07319341e032e3c6c36ec4d83     296     1   
c8c12d0843d056ad058d51fd96b360f5     308     1   
c7afef7aa25e055763846fa0ec43d26d     347     1   

                                                    dataset_legend  \
b057a3e07319341e032e3c6c36ec4d83        #1 brain - sLASER R:N=25:1   
c8c12d0843d056ad058d51fd96b360f5  #0 brain - sLASER 20:1 resp trig   
c7afef7aa25e055763846fa0ec43d26d            #0 sLASER 10:2 TE=30ms   

                                                               dataset_raw_files[0]  \
b057a3e07319341e032e3c6c36ec4d83  /home/tangir/crmbm/acq_twix/296_ym_p1_brainmoe...   
c8c12d0843d056ad058d51fd96b360f5  /home/tangir/crmbm/acq_twix/308-rs-p1-moelle/m...   
c7afef7aa25e055763846fa0ec43d26d  /home/tangir/crmbm/acq_twix/347-re-p1-moelle/m...   

                                                               dataset_raw_files[1]  \
b057a3e07319341e032e3c6c36ec4d83  /home/tangir/crmbm/acq_twix/296_ym_p1_brainmoe...   
c8c12d0843d056ad058d51fd96b360f5  /home/tangir/crmbm/acq_twix/308-rs-p1-moelle/m...   
c7afef7aa25e055763846fa0ec43d26d  /home/tangir/crmbm/acq_twix/347-re-p1-moelle/m...   

                                                               dataset_raw_data_obj  \
b057a3e07319341e032e3c6c36ec4d83  [(689.0669802502591-136.65124370561344j), (671...   
c8c12d0843d056ad058d51fd96b360f5  [(813.0401020344693-48.68837082080384j), (795....   
c7afef7aa25e055763846fa0ec43d26d  [(309.48049560871294+61.897647154302284j), (27...   

                                  dataset_raw_data__dt  dataset_raw_data__f0  \
b057a3e07319341e032e3c6c36ec4d83                0.0001            297.206367   
c8c12d0843d056ad058d51fd96b360f5                0.0001            297.206456   
c7afef7aa25e055763846fa0ec43d26d                0.0001            297.206385   

                                  dataset_raw_data__te  dataset_raw_data__tr  \
b057a3e07319341e032e3c6c36ec4d83                 49.96                3500.0   
c8c12d0843d056ad058d51fd96b360f5                 49.96                3000.0   
c7afef7aa25e055763846fa0ec43d26d                 30.28                3660.0   

                                  ...  \
b057a3e07319341e032e3c6c36ec4d83  ...   
c8c12d0843d056ad058d51fd96b360f5  ...   
c7afef7aa25e055763846fa0ec43d26d  ...   

                                  reco_pipeline_analyze_job_list[3]_POI_shift_range_ppm[1]  \
b057a3e07319341e032e3c6c36ec4d83                                                5.2          
c8c12d0843d056ad058d51fd96b360f5                                                5.2          
c7afef7aa25e055763846fa0ec43d26d                                                5.2          

                                 reco_pipeline_analyze_job_list[3]_POI_shift_true_ppm  \
b057a3e07319341e032e3c6c36ec4d83                                                4.7     
c8c12d0843d056ad058d51fd96b360f5                                                4.7     
c7afef7aa25e055763846fa0ec43d26d                                                4.7     

                                 reco_pipeline_analyze_job_list[3]_display  \
b057a3e07319341e032e3c6c36ec4d83                                     False   
c8c12d0843d056ad058d51fd96b360f5                                     False   
c7afef7aa25e055763846fa0ec43d26d                                     False   

                                 reco_pipeline_analyze_job_list[3]_display_range_ppm[0]  \
b057a3e07319341e032e3c6c36ec4d83                                                  1       
c8c12d0843d056ad058d51fd96b360f5                                                  1       
c7afef7aa25e055763846fa0ec43d26d                                                  1       

                                 reco_pipeline_analyze_job_list[3]_display_range_ppm[1]  \
b057a3e07319341e032e3c6c36ec4d83                                                  6       
c8c12d0843d056ad058d51fd96b360f5                                                  6       
c7afef7aa25e

## Final df
For SC and brain

In [12]:
# using previously filtered db
df_sc = df_onescan_per_study
df_sc_all_slaser = df_slaser
df_brain = df_brain_onescan_per_study

## Free some memory

In [13]:
def clean_mem(dir_result, except_list):
    for var_name in dir_result:
        if(eval("type(" + var_name + ")") == pd.DataFrame and var_name not in except_list):
            del globals()[var_name]
            
clean_mem(dir(), ["df_sc", "df_sc_all_slaser", "df_brain"])            
df_sc.info(memory_usage='deep')
df_sc_all_slaser.info(memory_usage='deep')
df_brain.info(memory_usage='deep')

<class 'pandas.core.frame.DataFrame'>
Index: 22 entries, 2fff316122fc89a0b4d1f918f6cd62d8 to 45b70edaa2460689b120a7ed10a1f6e1
Columns: 3111 entries, patient to dataset_water_signal
dtypes: datetime64[ns](30), float64(1933), object(1148)
memory usage: 1.4 MB
<class 'pandas.core.frame.DataFrame'>
Index: 40 entries, 405976f0de3db2b1ea8b83c3accc8994 to 45b70edaa2460689b120a7ed10a1f6e1
Columns: 3111 entries, patient to dataset_water_signal
dtypes: bool(80), datetime64[ns](30), float64(1789), int64(85), object(1127)
memory usage: 2.5 MB
<class 'pandas.core.frame.DataFrame'>
Index: 3 entries, b057a3e07319341e032e3c6c36ec4d83 to c7afef7aa25e055763846fa0ec43d26d
Columns: 1902 entries, patient to patient_study_id
dtypes: datetime64[ns](18), float64(968), object(916)
memory usage: 145.7 KB


# Cohort & anatomy

## [FIG1] Subject, height, weight, BMI, BFP
To check cohort characteristics

In [14]:
df = df_sc.loc[df_sc["study"] == 1]

this_df = df

this_df = this_df.rename(columns = {'dataset_raw_data__patient_weight':'Weight (kg)'})
this_df = this_df.rename(columns = {'dataset_raw_data__patient_height':'Height (m)'})
this_df = this_df.rename(columns = {'dataset_patient_bmi':'BMI'})
this_df = this_df.rename(columns = {'dataset_raw_data__patient_sex':'sex'})
 
g = sns.relplot(x="Weight (kg)", y="Height (m)", hue="BMI", palette=cm, style="sex", style_order=['F', 'M'],
                s=300, data=this_df)
g.ax.xaxis.grid(True)
g.ax.yaxis.grid(True)

x = df["dataset_raw_data__patient_weight"]
y = df["dataset_raw_data__patient_height"]
z = df["dataset_patient_bfp"]
zz = df["dataset_raw_data__patient_sex"]
g = sns.relplot(x=x, y=y, hue=z, palette=cm, style=zz, s=300)
g.ax.xaxis.grid(True)
g.ax.yaxis.grid(True)

print("Mean weight = %.2fkgs +/-%.2f " % (df["dataset_raw_data__patient_weight"].mean(),
                                          df["dataset_raw_data__patient_weight"].std()))
print("Mean height = %.2fm +/-%.2f " % (df["dataset_raw_data__patient_height"].mean(),
                                        df["dataset_raw_data__patient_height"].std()))
print("Mean BMI = %.2f +/-%.2f " % (df["dataset_patient_bmi"].mean(), 
                                    df["dataset_patient_bmi"].std()))

sex_counts = df["dataset_raw_data__patient_sex"].value_counts()
print("Sex = M(%d) F(%d)" % (sex_counts["M"], sex_counts["F"]))

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Mean weight = 57.07kgs +/-14.06 
Mean height = 1.66m +/-0.13 
Mean BMI = 20.34 +/-2.74 
Sex = M(5) F(10)


Well ok, the cohort is not super... A lot of women, small and thin. :s

## $B_1$ power (ref. voltage) & BMI
Do we have a dependence between reference voltage and BMI/BFP?

In [15]:
df = df_sc_all_slaser

x = df["dataset_raw_data__patient_weight"]
y = df["dataset_raw_data__patient_height"]
z = df["dataset_raw_data__sequence_vref"]
g = sns.relplot(x=x, y=y, hue=z, palette=cm, s=300)
g.ax.xaxis.grid(True)
g.ax.yaxis.grid(True)

x = df["dataset_patient_bmi"]
y = df["dataset_raw_data__sequence_vref"]
g = sns.JointGrid(x=x, y=y)
g.plot_joint(sns.regplot)
g.plot_marginals(sns.histplot, kde=True)
print("R = %.2f" % x.corr(y))

x = df["dataset_patient_bfp"]
y = df["dataset_raw_data__sequence_vref"]
g = sns.JointGrid(x=x, y=y)
g.plot_joint(sns.regplot)
g.plot_marginals(sns.histplot, kde=True)
print("R = %.2f" % x.corr(y))

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

R = 0.55


<IPython.core.display.Javascript object>

R = 0.55


Like for SC imaging, there is here a "strong" correlation between Vref and BMI/BFP.

## Voxel position & BMI
Does the voxel position change with BMI?

In [16]:
df = df_sc_all_slaser

# add voxel position to df
df["dataset_raw_data_posX_mm"] = np.array([o.position[0] for o in df["dataset_raw_data_obj"]])
df["dataset_raw_data_posY_mm"] = np.array([o.position[1] for o in df["dataset_raw_data_obj"]])
df["dataset_raw_data_posZ_mm"] = np.array([o.position[2] for o in df["dataset_raw_data_obj"]])

x = df["dataset_patient_bmi"]
y = -df["dataset_raw_data_posY_mm"]
g = sns.JointGrid(x=x, y=y)
g.plot_joint(sns.regplot)
g.plot_marginals(sns.histplot, kde=True)
print("R = %.2f" % x.corr(y))

x = df["dataset_patient_bfp"]
y = -df["dataset_raw_data_posY_mm"]
g = sns.JointGrid(x=x, y=y)
g.plot_joint(sns.regplot)
g.plot_marginals(sns.histplot, kde=True)
print("R = %.2f" % x.corr(y))

<IPython.core.display.Javascript object>

R = 0.63


<IPython.core.display.Javascript object>

R = 0.63


The voxel position in Y is nicely correlated with BMI/BFP. THe bigger you are, the higher will the voxel and therefore the further a way from the coil...

# Data quality

## [FIG2a] SNR & LW vs. BMI

In [17]:
df = df_sc_all_slaser

this_df = df
this_df = this_df.rename(columns = {'dataset_lw':'Water FWHM (Hz)'})
this_df = this_df.rename(columns = {'dataset_snr_norm':'SNR (u.a)'})
this_df = this_df.rename(columns = {'dataset_patient_bmi':'Subject BMI'})
g = sns.relplot(x="Water FWHM (Hz)", y="SNR (u.a)", hue="Subject BMI", palette=cm, s=300, data=this_df)
g.ax.xaxis.grid(True)
g.ax.yaxis.grid(True)

x = df["dataset_lw"]
y = df["dataset_snr_norm"]
z = df["dataset_patient_bfp"]
g = sns.relplot(x=x, y=y, hue=z, palette=cm, s=300)
g.ax.xaxis.grid(True)
g.ax.yaxis.grid(True)

# only SNR
x = df["dataset_patient_bmi"]
y = df["dataset_snr_norm"]
g = sns.JointGrid(x=x, y=y)
g.plot_joint(sns.regplot)
g.plot_marginals(sns.histplot, kde=True)
print("R = %.2f" % x.corr(y))

x = df["dataset_patient_bfp"]
y = df["dataset_snr_norm"]
g = sns.JointGrid(x=x, y=y)
g.plot_joint(sns.regplot)
g.plot_marginals(sns.histplot, kde=True)
print("R = %.2f" % x.corr(y))


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

R = -0.17


<IPython.core.display.Javascript object>

R = -0.17


## SNR vs. voxel position (BMI)

There could be some slight SNR dependance with BMI...

SNR is normalized by:
* voxel position in Y

Therefore
* SNR values are multiplied by $(1+\frac{y^2}{R^2})^{\frac{2}{3}}$ and multiplied by $(1+\frac{y_{mean}^2}{R^2})^{\frac{2}{3}}$

According to the Biot–Savart law (Jackson, 1975), cited in https://doi.org/10.1201/9781315107325, the distance relative to the RF loop surface coil impacts SNR with a $(1+\frac{y^2}{R^2})^{\frac{2}{3}}$ term. $y$ is the absolute distance between the voxel and the RF coil, $R$ is the coil radius. $y_{mean}$ is the average $y$ position over the whole group.

The problem is to evaluate this absolute distance to coil when I only know the voxel position relative to the magnet center... Let's take the lowest voxel position in the study group, probably for the thinnest subject and consider that we were 4cm away from the coil.

Ok, another problem is that we were using a multi-channel Rx spinal cord coil. What do I put for the radius? Assuing a 14cm radius coil... Big approximation.

In [18]:
df = df_sc_all_slaser

# does the Y position has an effect on SNR?
x = -df["dataset_raw_data_posY_mm"]
y = df["dataset_snr_norm"]
g = sns.JointGrid(x=x, y=y)
g.plot_joint(sns.regplot)
g.plot_marginals(sns.histplot, kde=True)
print("R = %.2f" % x.corr(y))

# Y voxel position normalization
min_dist_voxel_coil_mm = 40.0  # mm
coil_radius_mm = 140.0 / 2  # mm 
# looking for minimum Y position
max_pos = np.max(df["dataset_raw_data_posY_mm"])
df["dataset_raw_data_posY_mm_abs"] = -(df["dataset_raw_data_posY_mm"] - max_pos) + min_dist_voxel_coil_mm
mean_abs_y_pos = df["dataset_raw_data_posY_mm_abs"].mean()
# normalization
df["dataset_snr_norm_voxpos"] = df["dataset_snr_norm"] * np.power(1 + np.power(df["dataset_raw_data_posY_mm_abs"], 2) / np.power(coil_radius_mm, 2), 3/2)
df["dataset_snr_norm_voxpos"] = df["dataset_snr_norm_voxpos"] / np.power(1 + np.power(mean_abs_y_pos, 2) / np.power(coil_radius_mm, 2), 3/2)

x = df["dataset_lw"]
y = df["dataset_snr_norm_voxpos"]
z = df["dataset_patient_bmi"]
g = sns.relplot(x=x, y=y, hue=z, palette=cm, s=300)
g.ax.xaxis.grid(True)
g.ax.yaxis.grid(True)

x = df["dataset_lw"]
y = df["dataset_snr_norm_voxpos"]
z = df["dataset_patient_bfp"]
g = sns.relplot(x=x, y=y, hue=z, palette=cm, s=300)
g.ax.xaxis.grid(True)
g.ax.yaxis.grid(True)

# only SNR
x = df["dataset_patient_bmi"]
y = df["dataset_snr_norm_voxpos"]
g = sns.JointGrid(x=x, y=y)
g.plot_joint(sns.regplot)
g.plot_marginals(sns.histplot, kde=True)
print("R = %.2f" % x.corr(y))

x = df["dataset_patient_bfp"]
y = df["dataset_snr_norm_voxpos"]
g = sns.JointGrid(x=x, y=y)
g.plot_joint(sns.regplot)
g.plot_marginals(sns.histplot, kde=True)
print("R = %.2f" % x.corr(y))

<IPython.core.display.Javascript object>

R = -0.32


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

R = 0.27


<IPython.core.display.Javascript object>

R = 0.27


No more correlation in those last plots? Because we corected the SNR change due to voxel Y position.

To conclude, SNR is dependant on a few things:
* Of course, NA and voxel size
* But also Y voxel position and there those patient weight/height/BMI/BFP

# Signal stability, data quality & rejection

## SNR & signal stability
Before performing data rejection, the time evolution of the water peak amplitude, linewidth, chemical shift and phase are estimated. In a way, those estimations reflect signal stability or instability (due to physio motion). Could it affect the SNR?

In [19]:
df = df_sc

x = df["dataset_prerej_amplitude_std"].astype(np.float)
y = df["dataset_snr_norm"].astype(np.float)
g = sns.JointGrid(x=x, y=y)
g.plot_joint(sns.regplot)
g.plot_marginals(sns.histplot, kde=True)
print("R = %.2f" % x.corr(y))

x = df["dataset_prerej_linewidth_std"].astype(np.float)
y = df["dataset_snr_norm"].astype(np.float)
g = sns.JointGrid(x=x, y=y)
g.plot_joint(sns.regplot)
g.plot_marginals(sns.histplot, kde=True)
print("R = %.2f" % x.corr(y))

x = df["dataset_prerej_chemical_shift_std"].astype(np.float)
y = df["dataset_snr_norm"].astype(np.float)
g = sns.JointGrid(x=x, y=y)
g.plot_joint(sns.regplot)
g.plot_marginals(sns.histplot, kde=True)
print("R = %.2f" % x.corr(y))

x = df["dataset_prerej_phase_std"].astype(np.float)
y = df["dataset_snr_norm"].astype(np.float)
g = sns.JointGrid(x=x, y=y)
g.plot_joint(sns.regplot)
g.plot_marginals(sns.histplot, kde=True)
print("R = %.2f" % x.corr(y))

<IPython.core.display.Javascript object>

R = -0.40


<IPython.core.display.Javascript object>

R = -0.37


<IPython.core.display.Javascript object>

R = -0.12


<IPython.core.display.Javascript object>

R = -0.41


Nice results but not very significant...
SNR increases if the acquired signal is stable in terms of amplitude, linewidth, chemical shift and phase

## Data rejection & signal stability

In [20]:
df = df_sc

x = df["dataset_prerej_amplitude_std"]
y = df["dataset_rejection_rate_prct"]
g = sns.JointGrid(x=x, y=y)
g.plot_joint(sns.scatterplot)
g.plot_joint(sns.regplot)
g.plot_marginals(sns.histplot, kde=True)
print("R = %.2f" % x.corr(y))

x = df["dataset_prerej_linewidth_std"]
y = df["dataset_rejection_rate_prct"]
g = sns.JointGrid(x=x, y=y)
g.plot_joint(sns.scatterplot)
g.plot_joint(sns.regplot)
g.plot_marginals(sns.histplot, kde=True)
print("R = %.2f" % x.corr(y))

x = df["dataset_prerej_chemical_shift_std"]
y = df["dataset_rejection_rate_prct"]
g = sns.JointGrid(x=x, y=y)
g.plot_joint(sns.scatterplot)
g.plot_joint(sns.regplot)
g.plot_marginals(sns.histplot, kde=True)
print("R = %.2f" % x.corr(y))

x = df["dataset_prerej_phase_std"]
y = df["dataset_rejection_rate_prct"]
g = sns.JointGrid(x=x, y=y)
g.plot_joint(sns.scatterplot)
g.plot_joint(sns.regplot)
g.plot_marginals(sns.histplot, kde=True)
print("R = %.2f" % x.corr(y))

<IPython.core.display.Javascript object>

R = 0.45


<IPython.core.display.Javascript object>

R = 0.52


<IPython.core.display.Javascript object>

R = 0.22


<IPython.core.display.Javascript object>

R = 0.31


Interesting but not super significant, as usual. The amount of data we rejected during reconstruction depends on the signal stability (amplitude, **linewidth**, chemical shift and phase).

## Data rejection rate & acquisition time

In [21]:
df = df_sc

x = df["dataset_acqtime_eff"]
y = df["dataset_rejection_rate_prct"]
g = sns.JointGrid(x=x, y=y)
g.plot_joint(sns.scatterplot)
g.plot_joint(sns.regplot)
g.plot_marginals(sns.histplot, kde=True)
print("R = %.2f" % x.corr(y))

x = df["dataset_acqtime"]
y = df["dataset_rejection_rate_prct"]
g = sns.JointGrid(x=x, y=y)
g.plot_joint(sns.scatterplot)
g.plot_joint(sns.regplot)
g.plot_marginals(sns.histplot, kde=True)
print("R = %.2f" % x.corr(y))

<IPython.core.display.Javascript object>

R = 0.12


<IPython.core.display.Javascript object>

R = 0.27


Interesting but not super significant, as usual. The amount of data we rejected during reconstruction depends on the acquisition time (the longer you scan, the higher the probability to have some motion).

## Signal stability & heart beat
What about physio motion like heart and respiration? It should be reflected in the signal instabilities...

In [22]:
df = df_sc

x = df["dataset_heart_bpm"].astype(np.float)
y = df["dataset_prerej_amplitude_std"]
g = sns.JointGrid(x=x, y=y)
g.plot_joint(sns.scatterplot)
g.plot_joint(sns.regplot)
g.plot_marginals(sns.histplot, kde=True)
print("R = %.2f" % x.corr(y))

x = df["dataset_heart_bpm"].astype(np.float)
y = df["dataset_prerej_linewidth_std"]
g = sns.JointGrid(x=x, y=y)
g.plot_joint(sns.scatterplot)
g.plot_joint(sns.regplot)
g.plot_marginals(sns.histplot, kde=True)
print("R = %.2f" % x.corr(y))

x = df["dataset_heart_bpm"].astype(np.float)
y = df["dataset_prerej_chemical_shift_std"]
g = sns.JointGrid(x=x, y=y)
g.plot_joint(sns.scatterplot)
g.plot_joint(sns.regplot)
g.plot_marginals(sns.histplot, kde=True)
print("R = %.2f" % x.corr(y))

x = df["dataset_heart_bpm"].astype(np.float)
y = df["dataset_prerej_phase_std"]
g = sns.JointGrid(x=x, y=y)
g.plot_joint(sns.scatterplot)
g.plot_joint(sns.regplot)
g.plot_marginals(sns.histplot, kde=True)
print("R = %.2f" % x.corr(y))

<IPython.core.display.Javascript object>

R = -0.08


<IPython.core.display.Javascript object>

R = -0.25


<IPython.core.display.Javascript object>

R = 0.01


<IPython.core.display.Javascript object>

R = -0.20


Well, heart beat has apparently no influence on signal stability and therefore on our MRS data quality...

## Signal stability & respiration
Maybe respiration does explain the differences in signal stability between subjects?

In [23]:
df = df_sc

x = df["dataset_resp_bpm"].astype(np.float)
y = df["dataset_prerej_amplitude_std"]
g = sns.JointGrid(x=x, y=y)
g.plot_joint(sns.scatterplot)
g.plot_joint(sns.regplot)
g.plot_marginals(sns.histplot, kde=True)
print("R = %.2f" % x.corr(y))

x = df["dataset_resp_bpm"].astype(np.float)
y = df["dataset_prerej_linewidth_std"]
g = sns.JointGrid(x=x, y=y)
g.plot_joint(sns.scatterplot)
g.plot_joint(sns.regplot)
g.plot_marginals(sns.histplot, kde=True)
print("R = %.2f" % x.corr(y))

x = df["dataset_resp_bpm"].astype(np.float)
y = df["dataset_prerej_chemical_shift_std"]
g = sns.JointGrid(x=x, y=y)
g.plot_joint(sns.scatterplot)
g.plot_joint(sns.regplot)
g.plot_marginals(sns.histplot, kde=True)
print("R = %.2f" % x.corr(y))

x = df["dataset_resp_bpm"].astype(np.float)
y = df["dataset_prerej_phase_std"]
g = sns.JointGrid(x=x, y=y)
g.plot_joint(sns.scatterplot)
g.plot_joint(sns.regplot)
g.plot_marginals(sns.histplot, kde=True)
print("R = %.2f" % x.corr(y))

<IPython.core.display.Javascript object>

R = -0.53


<IPython.core.display.Javascript object>

R = -0.31


<IPython.core.display.Javascript object>

R = -0.30


<IPython.core.display.Javascript object>

R = -0.48


Nope, does not make any sense.

## Signal stability & BMI/BFP
Maybe big people move less or more ? Just curious...

In [24]:
df = df_sc

x = df["dataset_patient_bmi"].astype(np.float)
y = df["dataset_prerej_amplitude_std"]
g = sns.JointGrid(x=x, y=y)
g.plot_joint(sns.scatterplot)
g.plot_joint(sns.regplot)
g.plot_marginals(sns.histplot, kde=True)
print("R = %.2f" % x.corr(y))

x = df["dataset_patient_bmi"].astype(np.float)
y = df["dataset_prerej_linewidth_std"]
g = sns.JointGrid(x=x, y=y)
g.plot_joint(sns.scatterplot)
g.plot_joint(sns.regplot)
g.plot_marginals(sns.histplot, kde=True)
print("R = %.2f" % x.corr(y))

x = df["dataset_patient_bmi"].astype(np.float)
y = df["dataset_prerej_chemical_shift_std"]
g = sns.JointGrid(x=x, y=y)
g.plot_joint(sns.scatterplot)
g.plot_joint(sns.regplot)
g.plot_marginals(sns.histplot, kde=True)
print("R = %.2f" % x.corr(y))

x = df["dataset_patient_bmi"].astype(np.float)
y = df["dataset_prerej_phase_std"]
g = sns.JointGrid(x=x, y=y)
g.plot_joint(sns.scatterplot)
g.plot_joint(sns.regplot)
g.plot_marginals(sns.histplot, kde=True)
print("R = %.2f" % x.corr(y))

<IPython.core.display.Javascript object>

R = 0.06


<IPython.core.display.Javascript object>

R = 0.24


<IPython.core.display.Javascript object>

R = 0.01


<IPython.core.display.Javascript object>

R = 0.13


Nothing interesting here...

# [PAPER] Best, ok and worst spectra
According to SNR and LW and me

In [25]:
df = df_sc

k = 0
for this_index, this_row in df.iterrows():
    s = this_row["dataset_raw_data_obj"]
    if(s is None):
        s = this_row["dataset_dcm_data_obj"]
    
    s.set_display_offset(10000.0 * k)
    s.display_spectrum_1d(1000)
    k += 1

plt.legend('off')

<IPython.core.display.Javascript object>

# Minor questions and tests

## Does water LW from ref. data == WS data LW?

In [26]:
df = df_sc_all_slaser

x = df["dataset_lw"]
y = df["dataset_raw_ref-data-analysis-results_lw"]
g = sns.JointGrid(x=x, y=y, xlim=(0, 40), ylim=(0, 40))
g.plot_joint(sns.scatterplot)
g.plot_marginals(sns.histplot, kde=True)
print("R = %.2f" % x.corr(y))

<IPython.core.display.Javascript object>

R = 0.29


Yes, the LW measured on water is similar to the LW measured on NAA. This observation validates the approach of constraining the metabolite damping factors during the fit to the LW observed on water.

## Intensity of ref. water peak
Is it connected to MRS quality? Maybe reflects CSF contamination?

In [27]:
df = df_sc_all_slaser

x = df["dataset_raw_ref-data-analysis-results_snr"]
y = df["dataset_snr_norm"]
g = sns.JointGrid(x=x, y=y)
g.plot_joint(sns.scatterplot)
g.plot_joint(sns.regplot)
g.plot_marginals(sns.histplot, kde=True)
print("R = %.2f" % x.corr(y))

x = df["dataset_raw_ref-data-analysis-results_snr"]
y = df["dataset_lw"]
g = sns.JointGrid(x=x, y=y)
g.plot_joint(sns.scatterplot)
g.plot_joint(sns.regplot)
g.plot_marginals(sns.histplot, kde=True)
print("R = %.2f" % x.corr(y))


<IPython.core.display.Javascript object>

R = 0.08


<IPython.core.display.Javascript object>

R = 0.08


Nope, wrong intuition. The water intensity in the ref. data is not negative correlated to the SNR or LW. More the opposite actually...

## Artefact around 5 ppm
This artefact seems to increase when voxel size decreases in the $x$ dimension. The sLASER sequence is a *semi-*LASER sequence, meaning that not all spatial dimensions are selected using adiabatic RF pulses (like in LASER). The $x$ dimension is selected using a standard asymmetric RF sinc pulse while $y$ and $z$ are selected using HSn RF pulses.

But not only...

In [28]:
# look at all sLASER
df = df_sc_all_slaser
 
# voxel dimensions in X, Y and Z:
df["dataset_voxel_size_X"] = [o.voxel_size[0] for o in df["dataset_raw_data_obj"]]
df["dataset_voxel_size_Y"] = [o.voxel_size[1] for o in df["dataset_raw_data_obj"]]
df["dataset_voxel_size_Z"] = [o.voxel_size[2] for o in df["dataset_raw_data_obj"]]
df["dataset_voxel_size_min"] = [np.min(o.voxel_size) for o in df["dataset_raw_data_obj"]]

# normalization of artefact SNR
# VOI normalization
df["dataset_artefact_signal_norm"] = df["dataset_artefact_signal"] / df["dataset_voxel_vol_cm3"] * mean_voxel_vol
# NA normalization
df["dataset_artefact_signal_norm"] = df["dataset_artefact_signal_norm"] / np.sqrt(df["dataset_raw_data__data_rejection[0]_Post-rejection_na"]) * np.sqrt(na_norm)

# find big artefact datasets
plt.figure(120)
artefact_df = df.loc[df["dataset_artefact_signal_norm"] > 15000.0]
for s in artefact_df["dataset_raw_data_obj"]:
    s.display_spectrum_1d(1200)

x = df["dataset_voxel_size_min"]
y = df["dataset_artefact_signal_norm"]
z = df["dataset_patient_bmi"]
g = sns.relplot(x=x, y=y, hue=z, palette=cm, s=200)
g.ax.xaxis.grid(True)
g.ax.yaxis.grid(True)
g.ax.set_yscale('log')

x = df["dataset_raw_data_posY_mm"]
y = df["dataset_artefact_signal_norm"]
z = df["dataset_patient_bmi"]
g = sns.relplot(x=x, y=y, hue=z, palette=cm, s=200)
g.ax.xaxis.grid(True)
g.ax.yaxis.grid(True)
g.ax.set_yscale('log')

# maybe related to shimming?
first_order_shim_ranges = [-4000, 4000]
second_order_shim_ranges = [-13000, 13000]
shim_labels = ['X', 'Y', 'Z', 'Z2', 'ZX', 'ZY', 'Z2-Y2', 'XY']
shim_ranges = [first_order_shim_ranges, first_order_shim_ranges, first_order_shim_ranges, 
               second_order_shim_ranges, 
               second_order_shim_ranges, 
               second_order_shim_ranges, 
               second_order_shim_ranges, 
               second_order_shim_ranges]

df["dataset_shim_sum"] = 0
artefact_df["dataset_shim_sum"] = 0

df["dataset_shim_first_order_sum"] = 0
artefact_df["dataset_shim_first_order_sum"] = 0

df["dataset_shim_second_order_sum"] = 0
artefact_df["dataset_shim_second_order_sum"] = 0

for this_shim_index, this_shim_name, this_shim_range in zip(range(8), shim_labels, shim_ranges):
    df_key = "dataset_raw_data__sequence_shims[" + str(this_shim_index) + "]"
    x = df[df_key]
    y = df["dataset_artefact_signal_norm"]
    plt.figure()
    g = sns.regplot(x=x, y=y)
    plt.axvline(this_shim_range[0])
    plt.axvline(this_shim_range[1])
    g.set_yscale('log')
    print("R = %.2f for shim [%s]" % (x.corr(y), this_shim_name))
    
    # add up all shims
    if(this_shim_index < 3):
        df["dataset_shim_first_order_sum"] += df[df_key].abs()
        artefact_df["dataset_shim_first_order_sum"] += df[df_key].abs()
    else:
        df["dataset_shim_second_order_sum"] += df[df_key].abs()
        artefact_df["dataset_shim_second_order_sum"] += df[df_key].abs()
          
    df["dataset_shim_sum"] += df[df_key].abs()
    artefact_df["dataset_shim_sum"] += artefact_df[df_key].abs()

# high shim voltage in general?
x = df["dataset_shim_first_order_sum"]
y = df["dataset_artefact_signal_norm"]
plt.figure()
g = sns.regplot(x=x, y=y)
g.set_yscale('log')
print("R = %.2f" % x.corr(y))         
          
x = df["dataset_shim_second_order_sum"]
y = df["dataset_artefact_signal_norm"]
plt.figure()
g = sns.regplot(x=x, y=y)
g.set_yscale('log')
print("R = %.2f" % x.corr(y))
          
x = df["dataset_shim_sum"]
y = df["dataset_artefact_signal_norm"]
plt.figure()
g = sns.regplot(x=x, y=y)
g.set_yscale('log')
print("R = %.2f" % x.corr(y)) 

artefact_df[["patient_study_id", "dataset_artefact_signal"]]

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

R = 0.52


<IPython.core.display.Javascript object>

R = 0.53


patient_study_id  dataset_artefact_signal
scan_hash                                                                 
159437f4b7de93d40c7fef7853019df3            307_1              9565.560998
1baf6b702f39fefb5ad9e44179057ef7            307_1             12674.001356
01a46c3d8ebdb2912567745a61ef0d24            310_1             21843.056019
2195967ae34d5ef7dcfba4fc93a9e121            314_1             14092.724989
fe34c6902afd341a0c81de0a0b6d6373            316_1             29196.639993
5f9a42662bfe3586bee57f3ead964778            316_1             14912.680007
3c700829d5feb605285c5ef7cfad4055            319_1             10077.243117
f416f6db6cda52195e3b8046fc586ef2            319_1             14410.552598
2a9fe3c48c69e575db0a8eeeb202d44d            329_1             14961.806405
42063831757801c81193689ead085d37            304_2            245816.065807
8b934ce052f541a6923805395f44bfb8            304_2            197078.166632
fd2940e9489a5d28773792aeb95f54e7            336_2             10743.654300

I believe this artefact originates from badly localized signal in the $x$ dimension because of the poor efficiency of the half sinc selection pulse in inhomogenous $B_1$ situation (surface coil):
* This effect is increased when this bad pulse needs to select a small slice.
* Less clear but likely to happen, this effect is also increased when the VOI is far from the coil ($y$ position is high) and the $B_1$ inhomogeneity gets even more crazy.
* This problem could be connected to $B_0$ field homogeneity too! The worst cases were observed for maximum shim voltages... especially for 2nd order shim. Basically meaning that the shim adjustment failed and the operator (me) did not check, resulting in potential huge and shim-generated $B_0$ field inhomogeneity...

Related to $B_0$ and $B_1$ fields heterogeneity in general!

## Moving average window size
This reconstruction parameter had to be set manually a few times to avoid data corruption during frequency realignment and data rejection: 2, 4, 5... What does it depend on?

In [29]:
df = df_sc_all_slaser

# extract SNR before realignment

try_this_list = ["dataset_raw_analysis-results_zero-filling_snr",
                 "dataset_prerej_amplitude_mean",
                 "dataset_prerej_amplitude_std",
                "dataset_prerej_chemical_shift_mean",
                "dataset_prerej_chemical_shift_std",
                 "dataset_prerej_linewidth_mean",
                 "dataset_prerej_linewidth_std",
                "dataset_prerej_phase_mean",
                "dataset_prerej_phase_std",]

for ttl in try_this_list:
    x = df[ttl]
    y = df["reco_pipeline_job_realigning_moving_averages"]
    g = sns.JointGrid(x=x, y=y)
    g.plot_joint(sns.scatterplot)
    g.plot_marginals(sns.histplot, kde=True)
    print("R = %.2f" % x.corr(y))

    x = df[ttl]
    y = df["reco_pipeline_job_data-rejecting_moving_averages"]
    g = sns.JointGrid(x=x, y=y)
    g.plot_joint(sns.scatterplot)
    g.plot_marginals(sns.histplot, kde=True)
    print("R = %.2f" % x.corr(y))

<IPython.core.display.Javascript object>

R = -0.05


<IPython.core.display.Javascript object>

R = -0.20


<IPython.core.display.Javascript object>

...

/home/tangir/miniconda/envs/py37/lib/python3.7/site-packages/seaborn/distributions.py:305: UserWarning: Dataset has 0 variance; skipping density estimate.
  warnings.warn(msg, UserWarning)


<IPython.core.display.Javascript object>

R = 0.09


<IPython.core.display.Javascript object>

R = -0.04


* Seems that some datasets with low SNR needed moving averaging for the frequency realignment and the data rejection to work. Could we maybe find a SNR threshold or a simple relation between SNR and moving average window size so that it is set automatically? **Well NO, wrong hypothesis** :P
* What else? variation of peak properties ? They are actually estimated using the moving average window... 

Could not conclude anything... I still do not know how to adjust the averaging moving window size automatically :(

## SNR & NA
Curious to see if the usual SNR and $/sqrt(NA)$ dependence is observable

In [30]:
df = df_sc_all_slaser

x = df["dataset_raw_data__sequence_na"].astype(np.float)
y = df["dataset_snr_final"]
g = sns.JointGrid(x=x, y=y)
g.plot_joint(sns.scatterplot)


<IPython.core.display.Javascript object>

## sLASER protocols
Compare protocols 20/1, 10/2, 5/5 when possible in terms of SNR/LW

In [31]:
df = df_sc_all_slaser

# get the scans hash manually
df_slaser_tests = df.loc[(df["patient_study_id"] == "314_1")
                        | (df["patient_study_id"] == "316_1")
                        | (df["patient_study_id"] == "319_1")
                        | (df["patient_study_id"] == "329_1")
                        | (df["patient_study_id"] == "336_2")]

df_slaser_tests = df_slaser_tests.drop("967a1b8dace220e916df680759f31d84")

df_slaser_tests

patient  study               dataset_legend  \
scan_hash                                                                       
0a58f85af8c32d06cbbca74391447ad2      314      1               #0 sLASER 20:1   
2195967ae34d5ef7dcfba4fc93a9e121      314      1                #1 sLASER 5:5   
fe34c6902afd341a0c81de0a0b6d6373      316      1               #0 sLASER 20:1   
5f9a42662bfe3586bee57f3ead964778      316      1                #1 sLASER 5:5   
3c700829d5feb605285c5ef7cfad4055      319      1               #0 sLASER 20:1   
f416f6db6cda52195e3b8046fc586ef2      319      1               #1 sLASER 10:2   
fc8cb0e8f7b3747a10eeabc1cf8ab9fb      329      1               #0 sLASER 20:1   
2a9fe3c48c69e575db0a8eeeb202d44d      329      1               #1 sLASER 10:2   
355445d1bac5ee682c88f889b4c01d09      336      2  #0 sLASER 10/2 NA=64 notrig   
49872ea4c73b9206c804c4fdaa298ed9      336      2  #1 sLASER 20/1 NA=64 notrig   
fd2940e9489a5d28773792aeb95f54e7      336      2   #2 sLASER 5/5 NA=64 notrig   

                                                               dataset_raw_files[0]  \
scan_hash                                                                             
0a58f85af8c32d06cbbca74391447ad2  /home/tangir/crmbm/acq_twix/314-yt-p1-moelle/m...   
2195967ae34d5ef7dcfba4fc93a9e121  /home/tangir/crmbm/acq_twix/314-yt-p1-moelle/m...   
fe34c6902afd341a0c81de0a0b6d6373  /home/tangir/crmbm/acq_twix/316-ap-p1-moelle/m...   
5f9a42662bfe3586bee57f3ead964778  /home/tangir/crmbm/acq_twix/316-ap-p1-moelle/m...   
3c700829d5feb605285c5ef7cfad4055  /home/tangir/crmbm/acq_twix/319-fc-p1-moelle/m...   
f416f6db6cda52195e3b8046fc586ef2  /home/tangir/crmbm/acq_twix/319-fc-p1-moelle/m...   
fc8cb0e8f7b3747a10eeabc1cf8ab9fb  /home/tangir/crmbm/acq_twix/329-pi-p1-moelle/m...   
2a9fe3c48c69e575db0a8eeeb202d44d  /home/tangir/crmbm/acq_twix/329-pi-p1-moelle/m...   
355445d1bac5ee682c88f889b4c01d09  /home/tangir/crmbm/acq_twix/336-nb-p2-moelle/m...   
49872ea4c73b9206c804c4fdaa298ed9  /home/tangir/crmbm/acq_twix/336-nb-p2-moelle/m...   
fd2940e9489a5d28773792aeb95f54e7  /home/tangir/crmbm/acq_twix/336-nb-p2-moelle/m...   

                                                               dataset_raw_files[1]  \
scan_hash                                                                             
0a58f85af8c32d06cbbca74391447ad2  /home/tangir/crmbm/acq_twix/314-yt-p1-moelle/m...   
2195967ae34d5ef7dcfba4fc93a9e121  /home/tangir/crmbm/acq_twix/314-yt-p1-moelle/m...   
fe34c6902afd341a0c81de0a0b6d6373  /home/tangir/crmbm/acq_twix/316-ap-p1-moelle/m...   
5f9a42662bfe3586bee57f3ead964778  /home/tangir/crmbm/acq_twix/316-ap-p1-moelle/m...   
3c700829d5feb605285c5ef7cfad4055  /home/tangir/crmbm/acq_twix/319-fc-p1-moelle/m...   
f416f6db6cda52195e3b8046fc586ef2  /home/tangir/crmbm/acq_twix/319-fc-p1-moelle/m...   
fc8cb0e8f7b3747a10eeabc1cf8ab9fb  /home/tangir/crmbm/acq_twix/329-pi-p1-moelle/m...   
2a9fe3c48c69e575db0a8eeeb202d44d  /home/tangir/crmbm/acq_twix/329-pi-p1-moelle/m...   
355445d1bac5ee682c88f889b4c01d09  /home/tangir/crmbm/acq_twix/336-nb-p2-moelle/m...   
49872ea4c73b9206c804c4fdaa298ed9  /home/tangir/crmbm/acq_twix/336-nb-p2-moelle/m...   
fd2940e9489a5d28773792aeb95f54e7  /home/tangir/crmbm/acq_twix/336-nb-p2-moelle/m...   

                                                               dataset_raw_data_obj  \
scan_hash                                                                             
0a58f85af8c32d06cbbca74391447ad2  [(730.3440293819107-125.91066233625389j), (712...   
2195967ae34d5ef7dcfba4fc93a9e121  [(1008.4807903081726-17.76038805871182j), (881...   
fe34c6902afd341a0c81de0a0b6d6373  [(526.3710825321402-109.50225527879674j), (518...   
5f9a42662bfe3586bee57f3ead964778  [(535.8489858681635+21.802746814175052j), (534...   
3c700829d5feb605285c5ef7cfad4055  [(1208.0387209839266-395.25782076094237j), (12...   
f416f6db6cda52195e3b8046fc586ef2  [(1760.5827174966569-749.9357520232237j), (188...   
fc8cb0e8f7b3747a10ee

In [32]:
df_slaser_results = pd.DataFrame(columns=["patient_study_id",
                 "r20_snr",
                 "r20_lw",
                 "r20_te",
                 "r10_snr",
                 "r10_lw",
                 "r10_te",
                 "r5_snr",
                 "r5_lw",
                 "r5_te"])

df_slaser_results = df_slaser_results.set_index("patient_study_id")

# initialize
for this_index, this_row in df_slaser_tests.iterrows():
    this_patient_study_id = this_row["patient_study_id"]
    df_slaser_results.loc[this_patient_study_id] = [np.nan] * 9

# complete
for this_index, this_row in df_slaser_tests.iterrows():
    this_patient_study_id = this_row["patient_study_id"]
    this_r = this_row["dataset_raw_data__sequence_pulse_rfc_r"]
    if(this_r >= 20):
        df_slaser_results.loc[this_patient_study_id]["r20_snr"] = this_row["dataset_snr_norm"]
        df_slaser_results.loc[this_patient_study_id]["r20_lw"] = this_row["dataset_lw"]
        df_slaser_results.loc[this_patient_study_id]["r20_te"] = this_row["dataset_raw_data__sequence_te"]

    elif(this_r == 10):
        df_slaser_results.loc[this_patient_study_id]["r10_snr"] = this_row["dataset_snr_norm"]
        df_slaser_results.loc[this_patient_study_id]["r10_lw"] = this_row["dataset_lw"]
        df_slaser_results.loc[this_patient_study_id]["r10_te"] = this_row["dataset_raw_data__sequence_te"]

    elif(this_r == 5):
        df_slaser_results.loc[this_patient_study_id]["r5_snr"] = this_row["dataset_snr_norm"]
        df_slaser_results.loc[this_patient_study_id]["r5_lw"] = this_row["dataset_lw"]
        df_slaser_results.loc[this_patient_study_id]["r5_te"] = this_row["dataset_raw_data__sequence_te"]

df_slaser_results

r20_snr   r20_lw r20_te  r10_snr   r10_lw r10_te   r5_snr  \
patient_study_id                                                              
314_1             41.2369   16.276  41.68      NaN      NaN    NaN  38.7641   
316_1             14.2352  17.9036  45.96      NaN      NaN    NaN  19.1433   
319_1             27.8628  11.3932  62.96  45.9123  13.0208  38.96      NaN   
329_1             40.6484  19.5312  45.96  52.6085  21.1589  29.96      NaN   
336_2             24.1629  11.3932  52.36   18.048  19.5312  32.28  25.8735   

                    r5_lw  r5_te  
patient_study_id                  
314_1              16.276  19.96  
316_1             13.0208  21.16  
319_1                 NaN    NaN  
329_1                 NaN    NaN  
336_2             19.5312  22.68

In [33]:
# replace 0 by nan
df_slaser_results = df_slaser_results.replace(0, np.nan)

# estimate relative changes of all this
df_slaser_results["r20_2_r10_snr_prct"] = (df_slaser_results["r10_snr"] - df_slaser_results["r20_snr"]) / df_slaser_results["r20_snr"] * 100
df_slaser_results["r20_2_r10_lw"] = df_slaser_results["r10_lw"] - df_slaser_results["r20_lw"]
df_slaser_results["r20_2_r10_te"] = df_slaser_results["r10_te"] - df_slaser_results["r20_te"]
#
df_slaser_results["r20_2_r5_snr_prct"] = (df_slaser_results["r5_snr"] - df_slaser_results["r20_snr"]) / df_slaser_results["r20_snr"] * 100
df_slaser_results["r20_2_r5_lw"] = df_slaser_results["r5_lw"] - df_slaser_results["r20_lw"]
df_slaser_results["r20_2_r5_te"] = df_slaser_results["r5_te"] - df_slaser_results["r20_te"]

# display
plt.figure()
y=df_slaser_results[["r20_2_r10_snr_prct", "r20_2_r5_snr_prct"]]
sns.boxplot(data=y)

plt.figure()
y=df_slaser_results[["r20_2_r10_lw", "r20_2_r5_lw"]]
sns.boxplot(data=y)

plt.figure()
y=df_slaser_results[["r20_2_r10_te", "r20_2_r5_te"]]
sns.boxplot(data=y)


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<AxesSubplot:>

Interesting... I see that the R=20/1 is maybe not the best protocol to use... 
* The SNR is increased when switching to R=10/2, the LW looks unchanged
* The SNR is not really increased when switching to R=5 (starting to suffer from bad selectivity ?)
* The TE is reduced in both cases quite a lot >20ms

Seems I should have used 10/2 as the standard protocol. In theory less adiabatic but gives a shorter TE and higher SNR (probably connected but not sure when looking at the 5/5 results).

However, I need to find or remember why I used the 20/1 most of the time to justify in the paper. First let's see the proportion of this and that protocol in the P1/P2 data. In theory, the 10/2 scans should remain because the highest SNR scan per study was kept.

In [34]:
df = df_sc

df_20 = df.loc[df["dataset_raw_data__sequence_pulse_rfc_r"] >= 20]
df_10 = df.loc[df["dataset_raw_data__sequence_pulse_rfc_r"] == 10]
df_5 = df.loc[df["dataset_raw_data__sequence_pulse_rfc_r"] == 5]

print("* P1 and P2 scans represent %d datasets" % len(df))
print("* sLASER R>=20 was used %d times (%.2f%%)" % (len(df_20), len(df_20)/len(df) * 100))
print("* sLASER R==10 was used %d times (%.2f%%)" % (len(df_10), len(df_10)/len(df) * 100))
print("* sLASER R==5 was used %d times (%.2f%%)" % (len(df_5), len(df_5)/len(df) * 100))

df

* P1 and P2 scans represent 22 datasets
* sLASER R>=20 was used 16 times (72.73%)
* sLASER R==10 was used 5 times (22.73%)
* sLASER R==5 was used 1 times (4.55%)


patient study  \
2fff316122fc89a0b4d1f918f6cd62d8     300     1   
1baf6b702f39fefb5ad9e44179057ef7     307     1   
a2b582b37a04bd4efc43138368bc0b96     308     1   
01a46c3d8ebdb2912567745a61ef0d24     310     1   
7cb024e470b0b2b072436635a19a1c00     311     1   
9f8067ea065153da5b3a352d58f6ca23     313     1   
0a58f85af8c32d06cbbca74391447ad2     314     1   
5f9a42662bfe3586bee57f3ead964778     316     1   
f416f6db6cda52195e3b8046fc586ef2     319     1   
b9875913db5c0f321922f819401cc02e     328     1   
fc8cb0e8f7b3747a10eeabc1cf8ab9fb     329     1   
2e9c959e58727727c1576108fb6ef2b9     336     1   
afb10548c794ebbf8bd304be1f52b0c1     338     1   
ef31f01b58b8279ef0df239b6d15a055     300     2   
62f4072c25c940cd1bfcb41a560749e2     349     1   
75ae13bc44bf3d55f5be46d4c59df84d     311     2   
967a1b8dace220e916df680759f31d84     336     2   
90d883145e25fe54b74b05c16b56ace1     319     2   
e8481853cde6f05d66b1c43d8dd00e40     313     2   
da13ac26d45806eaced75e7dd71df1f3     333     1   
e2c8b162388ff1d24dca288885b87e4b     314     2   
45b70edaa2460689b120a7ed10a1f6e1     349     2   

                                                     dataset_legend  \
2fff316122fc89a0b4d1f918f6cd62d8            #1 sLASER R:N=25:1 trig   
1baf6b702f39fefb5ad9e44179057ef7  #3 sLASER 10:2 repos. + resp trig   
a2b582b37a04bd4efc43138368bc0b96           #0 sLASER 20:1 resp trig   
01a46c3d8ebdb2912567745a61ef0d24                     #0 sLASER 20:1   
7cb024e470b0b2b072436635a19a1c00                     #0 sLASER 20:1   
9f8067ea065153da5b3a352d58f6ca23                     #0 sLASER 20:1   
0a58f85af8c32d06cbbca74391447ad2                     #0 sLASER 20:1   
5f9a42662bfe3586bee57f3ead964778                      #1 sLASER 5:5   
f416f6db6cda52195e3b8046fc586ef2                     #1 sLASER 10:2   
b9875913db5c0f321922f819401cc02e                     #0 sLASER 20:1   
fc8cb0e8f7b3747a10eeabc1cf8ab9fb                     #0 sLASER 20:1   
2e9c959e58727727c1576108fb6ef2b9                     #0 sLASER 20:1   
afb10548c794ebbf8bd304be1f52b0c1                  #0 sLASER 20:1 WS   
ef31f01b58b8279ef0df239b6d15a055      #0 sLASER 20:1 (REF with OVS)   
62f4072c25c940cd1bfcb41a560749e2      #0 sLASER 10:2 (REF with OVS)   
75ae13bc44bf3d55f5be46d4c59df84d         #0 sLASER 20/1 NA=128 trig   
967a1b8dace220e916df680759f31d84         #0 sLASER 20/1 NA=128 trig   
90d883145e25fe54b74b05c16b56ace1          #0 sLASER 10/2 NA=64 trig   
e8481853cde6f05d66b1c43d8dd00e40                     #0 sLASER 20/1   
da13ac26d45806eaced75e7dd71df1f3                     #0 sLASER 20/1   
e2c8b162388ff1d24dca288885b87e4b              #0 sLASER 20/1 NA=128   
45b70edaa2460689b120a7ed10a1f6e1              #0 sLASER 10/2 NA=128   

                                                               dataset_raw_files[0]  \
2fff316122fc89a0b4d1f918f6cd62d8  /home/tangir/crmbm/acq_twix/300-pm-p1-moelle/m...   
1baf6b702f39fefb5ad9e44179057ef7  /home/tangir/crmbm/acq_twix/307-AP-P1-MOELLE/m...   
a2b582b37a04bd4efc43138368bc0b96  /home/tangir/crmbm/acq_twix/308-rs-p1-moelle/m...   
01a46c3d8ebdb2912567745a61ef0d24  /home/tangir/crmbm/acq_twix/310-mg-p1-moelle/m...   
7cb024e470b0b2b072436635a19a1c00  /home/tangir/crmbm/acq_twix/311-sl-p1-moelle/m...   
9f8067ea065153da5b3a352d58f6ca23  /home/tangir/crmbm/acq_twix/313-ft-p1-moelle/m...   
0a58f85af8c32d06cbbca74391447ad2  /home/tangir/crmbm/acq_twix/314-yt-p1-moelle/m...   
5f9a42662bfe3586bee57f3ead964778  /home/tangir/crmbm/acq_twix/316-ap-p1-moelle/m...   
f416f6db6cda52195e3b8046fc586ef2  /home/tangir/crmbm/acq_twix/319-fc-p1-moelle/m...   
b9875913db5c0f321922f819401cc02e  /home/tangir/crmbm/acq_twix/328-af-p1-moelle/m...   
fc8cb0e8f7b3747a10eeabc1cf8ab9fb  /home/tangir/crmbm/acq_twix/329-pi-p1-moelle/m...   
2e9c959e58727727c1576108fb6ef2b9  /home/tangir/crmbm/acq_twix/336-nb-p1-moelle/m...   
afb10548c794ebbf8bd304be1f52b0c1  /home/tangir/crmbm/acq_twix/338-ro-p1-moelle/m...   
ef31f01b58b8279ef0df239b6d15a0

Ok, and when did I prefer using this or that protocol. Did it depend on Vref, BMI ? 

In [35]:
x = df["dataset_patient_bmi"]
y = df["dataset_raw_data__sequence_pulse_rfc_r"]
g = sns.JointGrid(x=x, y=y)
g.plot_joint(sns.scatterplot)
g.plot_joint(sns.regplot)
g.plot_marginals(sns.histplot, kde=True)
print("R = %.2f" % x.corr(y))

x = df["dataset_raw_data__sequence_vref"]
y = df["dataset_raw_data__sequence_pulse_rfc_r"]
g = sns.JointGrid(x=x, y=y)
g.plot_joint(sns.scatterplot)
g.plot_joint(sns.regplot)
g.plot_marginals(sns.histplot, kde=True)
print("R = %.2f" % x.corr(y))


<IPython.core.display.Javascript object>

R = -0.36


<IPython.core.display.Javascript object>

R = -0.41


Ok makes sense. Since I was preferably scanning at R=20, I reduced R when BMI/Vref was too high (~300V). So it's not really like I had a choice.

But still I should performed R=10 systematically, it gives lower TE and stronger SNR. This was probably not the case in vitro because of long T2s...

It would be nice to estimate spectral quality with more than just SNR and LW. I suspect artefacts, lipids and shit showing up when reducing R because of bad selectivity and voxel contamination.

# [PAPER] Shimming: what is the best? 1st vs. 2nd order?
- Did 2nd order shim help? Extracting data from notebooks.

In [36]:
df = df_sc

# found this in my labbooks:
patient_list = [313,     319,     328, 329, 333, 336,  338,  300,    311,  336,  319,  313,  314,  349  ]
study_list = [    1,       1,       1,   1,   1,   1,    1,    2,      2,    1,    2,    2,    2,    2  ]
lw_linear = [    45,      25,      25,  30,  45,  30,   25,   35, np.nan,  np.nan,   39,   30,   20,   26  ]
lw_full = [      55,  np.nan,      40,  25,  50,  60,   35, 37.5,     25,   27,  np.nan,   50,   25,   30  ]

# keep only patient and study present in df
patient_list2 = []
study_list2 = []
lw_linear2 = []
lw_full2 = []
for p, s, lw1, lw2 in zip(patient_list, study_list, lw_linear, lw_full):
    if(p in df["patient"].to_list() and s in df.loc[df["patient"] == p]["study"].to_list()):
        patient_list2.append(p)
        study_list2.append(s)
        lw_linear2.append(lw1)
        lw_full2.append(lw2)

lw_linear2 = np.array(lw_linear2)
lw_full2 = np.array(lw_full2)
lw_diff2 = lw_full2 - lw_linear2
lw_diff2 = lw_diff2[~np.isnan(lw_diff2)]
print("In average, there was a %.2f +/- %.2f Hz change for the water LW when going from 1st to 2nd order shimming!" % (lw_diff2.mean(),lw_diff2.std()))


In average, there was a 9.65 +/- 9.44 Hz change for the water LW when going from 1st to 2nd order shimming!


# Scan-time, number of averages and data rejection

## Theoretical, effective (gated) and post-cor. acquisition duration
Compare theory, effective acquisition durations and "useful" acquisition durations (post-correction)

In [37]:
df = df_sc

# calculating usefull acqusition time post-correction
df["dataset_acqtime_eff_usefull"] = df["dataset_acqtime_eff"] - (df["dataset_acqtime_eff"] * df["dataset_rejection_rate_prct"] / 100.0)

# make a nice stackplot for each scan with: effective, and usefull
plt.figure()
sns.set_color_codes("pastel")
sns.barplot(x=df["dataset_acqtime_eff"], y=df["patient_study_id"],
            label="dataset_acqtime_eff", color="b")
sns.set_color_codes("muted")
sns.barplot(x=df["dataset_acqtime_eff_usefull"], y=df["patient_study_id"],
            label="dataset_acqtime_eff_usefull", color="b")


<IPython.core.display.Javascript object>

<AxesSubplot:xlabel='dataset_acqtime_eff_usefull', ylabel='patient_study_id'>

In [38]:
# to summarize into one bargraph:
# relative gain estimations between
# theory and effective durations
# effective durations and post-corrected durations

df["dataset_acqtime_eff_gain_prct"] = (df["dataset_acqtime_eff"] - df["dataset_acqtime"]) / df["dataset_acqtime"] * 100.0
df["dataset_acqtime_eff_usefull_gain_prct"] = (df["dataset_acqtime_eff_usefull"] - df["dataset_acqtime_eff"]) / df["dataset_acqtime_eff"] * 100.0
df["dataset_acqtime_eff_usefull_gain_prct_full"] = 100.0

plt.figure()
y = df["dataset_acqtime_eff_usefull_gain_prct_full"]
sns.set_color_codes("pastel")
sns.barplot(x=y, label="100%", color="b")

y = 100 + df["dataset_acqtime_eff_usefull_gain_prct"]
sns.set_color_codes("muted")
sns.barplot(x=y, label="dataset_acqtime_eff_usefull_gain_prct", color="b")


<IPython.core.display.Javascript object>

<AxesSubplot:xlabel='dataset_acqtime_eff_usefull_gain_prct'>

## Ideal acquisition time?
Any idea of how long shoud we scan?
Does it depend on SNR (I hope!) or BMI?

In [39]:
df = df_sc

x = df["dataset_acqtime"]
y = df["dataset_acqtime_eff"]
g = sns.JointGrid(x=x, y=y)
g.plot_joint(sns.regplot)
g.plot_marginals(sns.histplot, kde=True)
print("R = %.2f" % x.corr(y))

x = df["dataset_acqtime"]
y = df["dataset_acqtime_eff"]
z = df["dataset_patient_bfp"]
g = sns.relplot(x=x, y=y, hue=z, palette=cm, s=300)
g.ax.xaxis.grid(True)
g.ax.yaxis.grid(True)

x = df["dataset_acqtime_eff"]
y = df["dataset_patient_bmi"]
g = sns.JointGrid(x=x, y=y)
g.plot_joint(sns.regplot)
g.plot_marginals(sns.histplot, kde=True)
print("R = %.2f" % x.corr(y))

x = df["dataset_acqtime_eff"]
y = df["dataset_snr_final"]
g = sns.JointGrid(x=x, y=y)
g.plot_joint(sns.regplot)
g.plot_marginals(sns.histplot, kde=True)
print("R = %.2f" % x.corr(y))

x = df["dataset_acqtime_eff"]
y = df["dataset_prerej_linewidth_std"]
g = sns.JointGrid(x=x, y=y)
g.plot_joint(sns.regplot)
g.plot_marginals(sns.histplot, kde=True)
print("R = %.2f" % x.corr(y))


<IPython.core.display.Javascript object>

R = 0.89


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

R = 0.12


<IPython.core.display.Javascript object>

R = 0.01


<IPython.core.display.Javascript object>

R = 0.24


This what we can see:
* fat subjects need longer scan time (actually constrained by SAR and long TR
* no correlation between SNR and acquisition time
* the longer we scan, the less stable is the signal...

## Group-averaged rejected spectrum
Average over all subjects the data rejected into one crappy spectrum

In [40]:
df = df_sc

#init
s_arr = None
dt_final = 0.0001

fig = plt.figure()
ax = fig.subplots()

# extract rej spectrum for each dataset
for s in df["dataset_raw_data__data_rejection[0]_Rejected spectrum_obj"]:
    if(type(s) is not np.float):
        # resample so that all data can be averaged
        old_t = np.arange(0, s.shape[0] * s.dt, s.dt)
        new_t = np.arange(0, s.shape[0] * dt_final, dt_final) 

        s_interp = np.interp(new_t, old_t, s)

        # convert to suspect
        s_MRSData = suspect.MRSData(s_interp, dt_final, s.f0)
        s_MRSData2 = s_MRSData.view(reco.MRSData2)        

        s_MRSData2 = s_MRSData2.correct_zerofill_nd()
        if(s_arr is None):
            s_arr = s
        else:
            s_arr = np.vstack((s_arr, s_MRSData2))

        ax.plot(s_MRSData2.frequency_axis_ppm(), np.real(s_MRSData2.spectrum()))

ax.grid('on')
ax.set_xlim(5, 0)
ax.set_xlabel("chemical shift (ppm)")
ax.set_ylabel("rejected spectra (real part)")

# make the average + std plot
s_mean = np.mean(s_arr, axis=0)
s_mean = suspect.MRSData(s_mean, dt_final, s.f0)
s_mean = s_mean.view(reco.MRSData2)

s_std = np.std(s_arr, axis=0)
s_std = suspect.MRSData(s_std, dt_final, s.f0)
s_std = s_std.view(reco.MRSData2)

fig = plt.figure()
ax = fig.subplots()
ax.plot(s_mean.frequency_axis_ppm(), np.real(s_mean.spectrum()))
ax.grid('on')
ax.set_xlim(5, 0)
ax.set_xlabel("chemical shift (ppm)")
ax.set_ylabel("average rejected spectra (real part)")


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Text(0, 0.5, 'average rejected spectra (real part)')

Looks bad:
* Many artefact peaks
* Lipids
* NAA, Cho, Cre residue at 2 and 3 ppm ! :(
* Not sure about the 3-4 ppm region
* Usual artefact 5-6ppm

## Frequency realignment & data rejection: gain in SNR & LW
- Evaluate data rejection approach with peak properties estimated before and after :)

In [41]:
df = df_sc

# extract SNR and LW estimation regarding frequency realignment and data rejection 
df["dataset_prerej_snr1"] = df["dataset_raw_data__data_rejection[0]_Pre-rejection_snr"]
df["dataset_prerej_snr2"] = df["dataset_raw_analysis-results_frequency realigning_snr"]
df["dataset_postrej_snr1"] = df["dataset_raw_data__data_rejection[0]_Post-rejection_snr"]
df["dataset_postrej_snr2"] = df["dataset_raw_analysis-results_data rejecting_snr"]
#
df["dataset_prerej_lw1"] = df["dataset_raw_data__data_rejection[0]_Pre-rejection_lw"]
df["dataset_prerej_lw2"] = df["dataset_raw_analysis-results_frequency realigning_lw"]
df["dataset_postrej_lw1"] = df["dataset_raw_data__data_rejection[0]_Post-rejection_lw"]
df["dataset_postrej_lw2"] = df["dataset_raw_analysis-results_data rejecting_lw"]
#
df["dataset_prerea_snr"] = df["dataset_raw_analysis-results_apodizing_snr"]
df["dataset_postrea_snr"] = df["dataset_raw_analysis-results_frequency realigning_snr"]
#
df["dataset_prerea_lw"] = df["dataset_raw_analysis-results_apodizing_lw"]
df["dataset_postrea_lw"] = df["dataset_raw_analysis-results_frequency realigning_lw"]

# SNR and LW gain calculation
df["dataset_gainrej_snr1"] = (df["dataset_postrej_snr1"] - df["dataset_prerej_snr1"]) / df["dataset_prerej_snr1"] * 100.0
df["dataset_gainrej_snr2"] = (df["dataset_postrej_snr2"] - df["dataset_prerej_snr2"]) / df["dataset_prerej_snr2"] * 100.0
df["dataset_gainrej_lw1"] = (df["dataset_postrej_lw1"] - df["dataset_prerej_lw1"])
df["dataset_gainrej_lw2"] = (df["dataset_postrej_lw2"] - df["dataset_prerej_lw2"])
#
df["dataset_gainrea_snr"] = (df["dataset_postrea_snr"] - df["dataset_prerea_snr"]) / df["dataset_prerea_snr"] * 100.0
df["dataset_gainrea_lw"] = (df["dataset_postrea_lw"] - df["dataset_prerea_lw"])

plt.figure()
y=df[["dataset_gainrej_snr1", "dataset_gainrej_snr2", "dataset_gainrea_snr"]]
sns.boxplot(data=y)

plt.figure()
y=df[["dataset_gainrej_lw1", "dataset_gainrej_lw2", "dataset_gainrea_lw"]]
sns.boxplot(data=y)


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<AxesSubplot:>

# Gating approaches
For subjects who were scanned with different gating methods
* compare final SNR and LW
* compare peak properties variability (before data rejection)

In [42]:
df = df_sc_all_slaser

# get the scans hash manually
df_gating_tests = df.loc[(df["patient_study_id"] == "300_1")
                        | (df["patient_study_id"] == "307_1")
                        | (df["patient_study_id"] == "311_2")
                        | (df["patient_study_id"] == "336_2")]
df_gating_tests

patient  study  \
scan_hash                                          
fb81785a61e346c7fdbb37479f312ca5      300      1   
2fff316122fc89a0b4d1f918f6cd62d8      300      1   
40ef3af628211f936a93c79adb00ac9d      307      1   
159437f4b7de93d40c7fef7853019df3      307      1   
4a3a0b1b9f85f1928b9bfb342358fef4      307      1   
1baf6b702f39fefb5ad9e44179057ef7      307      1   
75ae13bc44bf3d55f5be46d4c59df84d      311      2   
caf8ec7f9e1026afbfa1e2c41ba43539      311      2   
355445d1bac5ee682c88f889b4c01d09      336      2   
967a1b8dace220e916df680759f31d84      336      2   
49872ea4c73b9206c804c4fdaa298ed9      336      2   
fd2940e9489a5d28773792aeb95f54e7      336      2   

                                                     dataset_legend  \
scan_hash                                                             
fb81785a61e346c7fdbb37479f312ca5                 #0 sLASER R:N=25:1   
2fff316122fc89a0b4d1f918f6cd62d8            #1 sLASER R:N=25:1 trig   
40ef3af628211f936a93c79adb00ac9d        #0 sLASER 20:1 cardiac trig   
159437f4b7de93d40c7fef7853019df3           #1 sLASER 20:1 resp trig   
4a3a0b1b9f85f1928b9bfb342358fef4             #2 sLASER 20:1 no trig   
1baf6b702f39fefb5ad9e44179057ef7  #3 sLASER 10:2 repos. + resp trig   
75ae13bc44bf3d55f5be46d4c59df84d         #0 sLASER 20/1 NA=128 trig   
caf8ec7f9e1026afbfa1e2c41ba43539       #1 sLASER 20/1 NA=128 notrig   
355445d1bac5ee682c88f889b4c01d09        #0 sLASER 10/2 NA=64 notrig   
967a1b8dace220e916df680759f31d84         #0 sLASER 20/1 NA=128 trig   
49872ea4c73b9206c804c4fdaa298ed9        #1 sLASER 20/1 NA=64 notrig   
fd2940e9489a5d28773792aeb95f54e7         #2 sLASER 5/5 NA=64 notrig   

                                                               dataset_raw_files[0]  \
scan_hash                                                                             
fb81785a61e346c7fdbb37479f312ca5  /home/tangir/crmbm/acq_twix/300-pm-p1-moelle/m...   
2fff316122fc89a0b4d1f918f6cd62d8  /home/tangir/crmbm/acq_twix/300-pm-p1-moelle/m...   
40ef3af628211f936a93c79adb00ac9d  /home/tangir/crmbm/acq_twix/307-AP-P1-MOELLE/m...   
159437f4b7de93d40c7fef7853019df3  /home/tangir/crmbm/acq_twix/307-AP-P1-MOELLE/m...   
4a3a0b1b9f85f1928b9bfb342358fef4  /home/tangir/crmbm/acq_twix/307-AP-P1-MOELLE/m...   
1baf6b702f39fefb5ad9e44179057ef7  /home/tangir/crmbm/acq_twix/307-AP-P1-MOELLE/m...   
75ae13bc44bf3d55f5be46d4c59df84d  /home/tangir/crmbm/acq_twix/311-sl-p2-moelle/m...   
caf8ec7f9e1026afbfa1e2c41ba43539  /home/tangir/crmbm/acq_twix/311-sl-p2-moelle/m...   
355445d1bac5ee682c88f889b4c01d09  /home/tangir/crmbm/acq_twix/336-nb-p2-moelle/m...   
967a1b8dace220e916df680759f31d84  /home/tangir/crmbm/acq_twix/336-nb-p2-moelle/m...   
49872ea4c73b9206c804c4fdaa298ed9  /home/tangir/crmbm/acq_twix/336-nb-p2-moelle/m...   
fd2940e9489a5d28773792aeb95f54e7  /home/tangir/crmbm/acq_twix/336-nb-p2-moelle/m...   

                                                               dataset_raw_files[1]  \
scan_hash                                                                             
fb81785a61e346c7fdbb37479f312ca5  /home/tangir/crmbm/acq_twix/300-pm-p1-moelle/m...   
2fff316122fc89a0b4d1f918f6cd62d8  /home/tangir/crmbm/acq_twix/300-pm-p1-moelle/m...   
40ef3af628211f936a93c79adb00ac9d  /home/tangir/crmbm/acq_twix/307-AP-P1-MOELLE/m...   
159437f4b7de93d40c7fef7853019df3  /home/tangir/crmbm/acq_twix/307-AP-P1-MOELLE/m...   
4a3a0b1b9f85f1928b9bfb342358fef4  /home/tangir/crmbm/acq_twix/307-AP-P1-MOELLE/m...   
1baf6b702f39fefb5ad9e44179057ef7  /home/tangir/crmbm/acq_twix/307-AP-P1-MOELLE/m...   
75ae13bc44bf3d55f5be46d4c59df84d  /home/tangir/crmbm/acq_twix/311-sl-p2-moelle/m...   
caf8ec7f9e1026afbfa1e2c41ba43539  /home/tangir/crmbm/acq_twix/311-sl-p2-moelle/m...   
355445d1bac5ee682c88f889b4c01d09  /home/tangir/crmbm/acq_twix/336-nb-p2-moelle/m...   
967a1b8dace220e916df680759f31d84  /home/tangir/crmbm/acq_twix/336-nb-p2-moelle/m...   
49872ea4c73b9206c804c4fdaa298ed9  /home/tangir/

In [43]:
# remove some scans
df_gating_tests = df_gating_tests.drop("1baf6b702f39fefb5ad9e44179057ef7")
df_gating_tests = df_gating_tests.drop("fd2940e9489a5d28773792aeb95f54e7")
df_gating_tests = df_gating_tests.drop("355445d1bac5ee682c88f889b4c01d09")
df_gating_tests

patient  study  \
scan_hash                                          
fb81785a61e346c7fdbb37479f312ca5      300      1   
2fff316122fc89a0b4d1f918f6cd62d8      300      1   
40ef3af628211f936a93c79adb00ac9d      307      1   
159437f4b7de93d40c7fef7853019df3      307      1   
4a3a0b1b9f85f1928b9bfb342358fef4      307      1   
75ae13bc44bf3d55f5be46d4c59df84d      311      2   
caf8ec7f9e1026afbfa1e2c41ba43539      311      2   
967a1b8dace220e916df680759f31d84      336      2   
49872ea4c73b9206c804c4fdaa298ed9      336      2   

                                                dataset_legend  \
scan_hash                                                        
fb81785a61e346c7fdbb37479f312ca5            #0 sLASER R:N=25:1   
2fff316122fc89a0b4d1f918f6cd62d8       #1 sLASER R:N=25:1 trig   
40ef3af628211f936a93c79adb00ac9d   #0 sLASER 20:1 cardiac trig   
159437f4b7de93d40c7fef7853019df3      #1 sLASER 20:1 resp trig   
4a3a0b1b9f85f1928b9bfb342358fef4        #2 sLASER 20:1 no trig   
75ae13bc44bf3d55f5be46d4c59df84d    #0 sLASER 20/1 NA=128 trig   
caf8ec7f9e1026afbfa1e2c41ba43539  #1 sLASER 20/1 NA=128 notrig   
967a1b8dace220e916df680759f31d84    #0 sLASER 20/1 NA=128 trig   
49872ea4c73b9206c804c4fdaa298ed9   #1 sLASER 20/1 NA=64 notrig   

                                                               dataset_raw_files[0]  \
scan_hash                                                                             
fb81785a61e346c7fdbb37479f312ca5  /home/tangir/crmbm/acq_twix/300-pm-p1-moelle/m...   
2fff316122fc89a0b4d1f918f6cd62d8  /home/tangir/crmbm/acq_twix/300-pm-p1-moelle/m...   
40ef3af628211f936a93c79adb00ac9d  /home/tangir/crmbm/acq_twix/307-AP-P1-MOELLE/m...   
159437f4b7de93d40c7fef7853019df3  /home/tangir/crmbm/acq_twix/307-AP-P1-MOELLE/m...   
4a3a0b1b9f85f1928b9bfb342358fef4  /home/tangir/crmbm/acq_twix/307-AP-P1-MOELLE/m...   
75ae13bc44bf3d55f5be46d4c59df84d  /home/tangir/crmbm/acq_twix/311-sl-p2-moelle/m...   
caf8ec7f9e1026afbfa1e2c41ba43539  /home/tangir/crmbm/acq_twix/311-sl-p2-moelle/m...   
967a1b8dace220e916df680759f31d84  /home/tangir/crmbm/acq_twix/336-nb-p2-moelle/m...   
49872ea4c73b9206c804c4fdaa298ed9  /home/tangir/crmbm/acq_twix/336-nb-p2-moelle/m...   

                                                               dataset_raw_files[1]  \
scan_hash                                                                             
fb81785a61e346c7fdbb37479f312ca5  /home/tangir/crmbm/acq_twix/300-pm-p1-moelle/m...   
2fff316122fc89a0b4d1f918f6cd62d8  /home/tangir/crmbm/acq_twix/300-pm-p1-moelle/m...   
40ef3af628211f936a93c79adb00ac9d  /home/tangir/crmbm/acq_twix/307-AP-P1-MOELLE/m...   
159437f4b7de93d40c7fef7853019df3  /home/tangir/crmbm/acq_twix/307-AP-P1-MOELLE/m...   
4a3a0b1b9f85f1928b9bfb342358fef4  /home/tangir/crmbm/acq_twix/307-AP-P1-MOELLE/m...   
75ae13bc44bf3d55f5be46d4c59df84d  /home/tangir/crmbm/acq_twix/311-sl-p2-moelle/m...   
caf8ec7f9e1026afbfa1e2c41ba43539  /home/tangir/crmbm/acq_twix/311-sl-p2-moelle/m...   
967a1b8dace220e916df680759f31d84  /home/tangir/crmbm/acq_twix/336-nb-p2-moelle/m...   
49872ea4c73b9206c804c4fdaa298ed9  /home/tangir/crmbm/acq_twix/336-nb-p2-moelle/m...   

                                                               dataset_raw_data_obj  \
scan_hash                                                                             
fb81785a61e346c7fdbb37479f312ca5  [(426.508162270165-25.29576424165769j), (419.8...   
2fff316122fc89a0b4d1f918f6cd62d8  [(466.7910467092009+42.6625311942012j), (449.5...   
40ef3af628211f936a93c79adb00ac9d  [(407.49602726268415-207.9086346239237j), (425...   
159437f4b7de93d40c7fef7853019df3  [(498.05689346512656+329.8932319576538j), (420...   
4a3a0b1b9f85f1928b9bfb342358fef4  [(509.3192079352583+42.15127719925854j), (507....   
75ae13bc44bf3d55f5be46d4c59df84d  [(278.27531875958914-2.7295633846843037j), (26...   
caf8ec7f9e1026afbfa1e2c41ba43539  [(273.0080880478138+48.28108955825748j), (269....   
967a1b8dace220e916df680759f31d84  [

In [44]:
df_gating_results = pd.DataFrame(columns=["patient_study_id",
                 "notrig_dataset_snr_norm",
                 "notrig_dataset_lw",
                 "notrig_prerej_amplitude_std",
                 "notrig_prerej_linewidth_std",
                 "notrig_prerej_chemical_shift_std",
                 "notrig_prerej_phase_std",
                 "cardiac_dataset_snr_norm",
                 "cardiac_dataset_lw",
                 "cardiac_prerej_amplitude_std",
                 "cardiac_prerej_linewidth_std",
                 "cardiac_prerej_chemical_shift_std",
                 "cardiac_prerej_phase_std",
                 "resp_dataset_snr_norm",
                 "resp_dataset_lw",
                 "resp_prerej_amplitude_std",
                 "resp_prerej_linewidth_std",
                 "resp_prerej_chemical_shift_std",
                 "resp_prerej_phase_std"])
df_gating_results = df_gating_results.set_index("patient_study_id")

# initialize
for this_index, this_row in df_gating_tests.iterrows():
    this_patient_study_id = this_row["patient_study_id"]
    df_gating_results.loc[this_patient_study_id] = [np.nan] * 18

# complete
for this_index, this_row in df_gating_tests.iterrows():
    this_patient_study_id = this_row["patient_study_id"]
    this_gating = this_row["dataset_raw_data__sequence_gating_mode"]
    if(this_gating == sim.gating_signal_source.NO_GATING):
        df_gating_results.loc[this_patient_study_id]["notrig_dataset_snr_norm"] = this_row["dataset_snr_norm"]
        df_gating_results.loc[this_patient_study_id]["notrig_dataset_lw"] = this_row["dataset_lw"]
        df_gating_results.loc[this_patient_study_id]["notrig_prerej_amplitude_std"] = this_row["dataset_prerej_amplitude_std"]
        df_gating_results.loc[this_patient_study_id]["notrig_prerej_linewidth_std"] = this_row["dataset_prerej_linewidth_std"]
        df_gating_results.loc[this_patient_study_id]["notrig_prerej_chemical_shift_std"] = this_row["dataset_prerej_chemical_shift_std"]
        df_gating_results.loc[this_patient_study_id]["notrig_prerej_phase_std"] = this_row["dataset_prerej_phase_std"]

    elif(this_gating == sim.gating_signal_source.CARDIAC_GATING):
        df_gating_results.loc[this_patient_study_id]["cardiac_dataset_snr_norm"] = this_row["dataset_snr_norm"]
        df_gating_results.loc[this_patient_study_id]["cardiac_dataset_lw"] = this_row["dataset_lw"]
        df_gating_results.loc[this_patient_study_id]["cardiac_prerej_amplitude_std"] = this_row["dataset_prerej_amplitude_std"]
        df_gating_results.loc[this_patient_study_id]["cardiac_prerej_linewidth_std"] = this_row["dataset_prerej_linewidth_std"]
        df_gating_results.loc[this_patient_study_id]["cardiac_prerej_chemical_shift_std"] = this_row["dataset_prerej_chemical_shift_std"]
        df_gating_results.loc[this_patient_study_id]["cardiac_prerej_phase_std"] = this_row["dataset_prerej_phase_std"]

    elif(this_gating == sim.gating_signal_source.RESP_GATING):
        df_gating_results.loc[this_patient_study_id]["resp_dataset_snr_norm"] = this_row["dataset_snr_norm"]
        df_gating_results.loc[this_patient_study_id]["resp_dataset_lw"] = this_row["dataset_lw"]
        df_gating_results.loc[this_patient_study_id]["resp_prerej_amplitude_std"] = this_row["dataset_prerej_amplitude_std"]
        df_gating_results.loc[this_patient_study_id]["resp_prerej_linewidth_std"] = this_row["dataset_prerej_linewidth_std"]
        df_gating_results.loc[this_patient_study_id]["resp_prerej_chemical_shift_std"] = this_row["dataset_prerej_chemical_shift_std"]
        df_gating_results.loc[this_patient_study_id]["resp_prerej_phase_std"] = this_row["dataset_prerej_phase_std"]
             
df_gating_results

notrig_dataset_snr_norm notrig_dataset_lw  \
patient_study_id                                             
300_1                            32.3484           13.0208   
307_1                            35.7298           27.6693   
311_2                            32.4855           14.6484   
336_2                            24.1629           11.3932   

                 notrig_prerej_amplitude_std notrig_prerej_linewidth_std  \
patient_study_id                                                           
300_1                                24.6681                     4.58813   
307_1                                65.4348                     13.5994   
311_2                                 13.072                     2.44122   
336_2                                59.6622                     6.17274   

                 notrig_prerej_chemical_shift_std notrig_prerej_phase_std  \
patient_study_id                                                            
300_1                                           0                0.228364   
307_1                                   0.0249303                0.667752   
311_2                                   0.0039589                0.213035   
336_2                                   0.0954253                0.883059   

                 cardiac_dataset_snr_norm cardiac_dataset_lw  \
patient_study_id                                               
300_1                                 NaN                NaN   
307_1                             15.0791            22.7865   
311_2                                 NaN                NaN   
336_2                                 NaN                NaN   

                 cardiac_prerej_amplitude_std cardiac_prerej_linewidth_std  \
patient_study_id                                                             
300_1                                     NaN                          NaN   
307_1                                 43.4153                      5.45147   
311_2                                     NaN                          NaN   
336_2                                     NaN                          NaN   

                 cardiac_prerej_chemical_shift_std cardiac_prerej_phase_std  \
patient_study_id                                                              
300_1                                          NaN                      NaN   
307_1                                    0.0286077                 0.512939   
311_2                                          NaN                      NaN   
336_2                                          NaN                      NaN   

                 resp_dataset_snr_norm resp_dataset_lw  \
patient_study_id                                         
300_1                          35.7319         14.6484   
307_1                          25.1213         29.2969   
311_2                          30.3051         13.0208   
336_2                          27.5973         11.3932   

                 resp_prerej_amplitude_std resp_prerej_linewidth_std  \
patient_study_id                                                       
300_1                              34.1816                    7.9642   
307_1                              47.3168                   17.8939   
311_2                              13.0128                   1.92368   
336_2                              38.9949                   4.05722   

                 resp_prerej_chemical_shift_std resp_prerej_phase_std  
patient_study_id                                                       
300_1                                 0.0391588              0.291642  
307_1                                0.00596214              0.361885  
311_2                                0.00244201              0.224967  
336_2                                 0.0368152              0.562552

In [45]:
# replace 0 by nan
df_gating_results = df_gating_results.replace(0, np.nan)

# estimate relative changes of all this
df_gating_results["notrig2resp_dataset_snr_norm_prct"] = (df_gating_results["resp_dataset_snr_norm"] - df_gating_results["notrig_dataset_snr_norm"]) / df_gating_results["notrig_dataset_snr_norm"] * 100
df_gating_results["notrig2resp_dataset_lw"] = df_gating_results["resp_dataset_lw"] - df_gating_results["notrig_dataset_lw"]
df_gating_results["notrig2resp_prerej_amplitude_std_prct"] = (df_gating_results["resp_prerej_amplitude_std"] - df_gating_results["notrig_prerej_amplitude_std"]) / df_gating_results["notrig_prerej_amplitude_std"] * 100
df_gating_results["notrig2resp_prerej_linewidth_std_prct"] = (df_gating_results["resp_prerej_linewidth_std"] - df_gating_results["notrig_prerej_linewidth_std"]) / df_gating_results["notrig_prerej_linewidth_std"] * 100
df_gating_results["notrig2resp_prerej_chemical_shift_std_prct"] = (df_gating_results["resp_prerej_chemical_shift_std"] - df_gating_results["notrig_prerej_chemical_shift_std"]) / df_gating_results["notrig_prerej_chemical_shift_std"] * 100
df_gating_results["notrig2resp_prerej_phase_std_prct"] = (df_gating_results["resp_prerej_phase_std"] - df_gating_results["notrig_prerej_phase_std"]) / df_gating_results["notrig_prerej_phase_std"] * 100
#
df_gating_results["notrig2cardiac_dataset_snr_norm_prct"] = (df_gating_results["cardiac_dataset_snr_norm"] - df_gating_results["notrig_dataset_snr_norm"]) / df_gating_results["notrig_dataset_snr_norm"] * 100
df_gating_results["notrig2cardiac_dataset_lw"] = df_gating_results["cardiac_dataset_lw"] - df_gating_results["notrig_dataset_lw"]
df_gating_results["notrig2cardiac_prerej_amplitude_std_prct"] = (df_gating_results["cardiac_prerej_amplitude_std"] - df_gating_results["notrig_prerej_amplitude_std"]) / df_gating_results["notrig_prerej_amplitude_std"] * 100
df_gating_results["notrig2cardiac_prerej_linewidth_std_prct"] = (df_gating_results["cardiac_prerej_linewidth_std"] - df_gating_results["notrig_prerej_linewidth_std"]) / df_gating_results["notrig_prerej_linewidth_std"] * 100
df_gating_results["notrig2cardiac_prerej_chemical_shift_std_prct"] = (df_gating_results["cardiac_prerej_chemical_shift_std"] - df_gating_results["notrig_prerej_chemical_shift_std"]) / df_gating_results["notrig_prerej_chemical_shift_std"] * 100
df_gating_results["notrig2cardiac_prerej_phase_std_prct"] = (df_gating_results["cardiac_prerej_phase_std"] - df_gating_results["notrig_prerej_phase_std"]) / df_gating_results["notrig_prerej_phase_std"] * 100

# display
plt.figure()
y=df_gating_results[["notrig2resp_dataset_snr_norm_prct", "notrig2cardiac_dataset_snr_norm_prct"]]
sns.boxplot(data=y)

plt.figure()
y=df_gating_results[["notrig2resp_dataset_lw", "notrig2cardiac_dataset_lw"]]
sns.boxplot(data=y)

plt.figure()
y=df_gating_results[["notrig2resp_prerej_amplitude_std_prct", "notrig2cardiac_prerej_amplitude_std_prct"]]
sns.boxplot(data=y)

plt.figure()
y=df_gating_results[["notrig2resp_prerej_linewidth_std_prct", "notrig2cardiac_prerej_linewidth_std_prct"]]
sns.boxplot(data=y)

plt.figure()
y=df_gating_results[["notrig2resp_prerej_chemical_shift_std_prct", "notrig2cardiac_prerej_chemical_shift_std_prct"]]
sns.boxplot(data=y)

plt.figure()
y=df_gating_results[["notrig2resp_prerej_phase_std_prct", "notrig2cardiac_prerej_phase_std_prct"]]
sns.boxplot(data=y)


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<AxesSubplot:>

All this was hard to program... but interesting however poorly significant results:
* too few points for cardiac gating to conclude anything
* the use of resp gating increases signal stability during scan: all peak properties (amplitude, linewidth, chemical shift and phase) standard deviations are reduced
* however, the gain in SNR/LW is really poor when comparing resp to no trig. Need more subjects if I really want to show this.

# Save dataframes to files

In [46]:
df_sc.to_pickle("/home/tangir/crmbm/acq_db/sc_notebook.pkl")
df_brain.to_pickle("/home/tangir/crmbm/acq_db/brain_notebook.pkl")